TODO: all comments in English

- hg38 FASTA: /s/genomes/Gencode/Gencode_human/release_40/GRCh38.p13.genome.fa
- hg38 GTF: /s/genomes/Gencode/Gencode_human/release_40/gencode.v40.annotation.gtf.gz
- read FASTA: pyfaidx
- read GTF: pyranges
- Sequence dataloaders: Kipoiseq

# Import Dependencies

In [1]:
import pyranges as pr
import pandas as pd
import os
from pyfaidx import Fasta
import numpy as np
from Bio.Seq import Seq

pd.options.display.max_columns = None # to show all columns of the dataframe

# Read VCF files with GTEx variants (parts rn)

In [2]:
hg38_vcf_path = "/s/project/rep/processed/training_results_v15/gtex_v8/distinct_variants.valid_snp_indel.vcf/"
# hg19_vcf_path = "/s/project/rep/processed/training_results_v15/gtex_v8_old_dna/distinct_variants.valid_snp_indel.vcf/"

vcf_dir = hg38_vcf_path

In [3]:
def list_vcf_files(vcf_dir):
    all_files = os.listdir(vcf_dir)
    vcf_files = [os.path.join(vcf_dir, f) for f in all_files if f.endswith(".vcf") or f.endswith(".vcf.gz")]
    if len(vcf_files) == 0:
        raise FileNotFoundError(f"No VCF files found in the directory: {vcf_dir}")
    return vcf_files

vcf_files = list_vcf_files(vcf_dir)
print(vcf_files[0])

/s/project/rep/processed/training_results_v15/gtex_v8/distinct_variants.valid_snp_indel.vcf/part-00241-61a0abbf-fbf9-444f-8287-4e46ad4b9b7b-c000.vcf


In [4]:
def read_vcf(vcf_path):
    df = pd.read_csv(
        vcf_path,
        comment='#',
        sep='\t',
        header=None,
        names=['Chromosome', 'Start', 'ID', 'Ref', 'Alt', 'Qual', 'Filter', 'Info']
    )
    
    # Adjust coordinates
    df['Start'] = df['Start'] - 1
    df['End'] = df['Start'] + df['Ref'].str.len()
    
    gr = pr.PyRanges(df[['Chromosome', 'Start', 'End', 'ID', 'Ref', 'Alt', 'Qual', 'Filter', 'Info']])
    return gr

hg38_example = read_vcf(vcf_files[0])
hg38_example

+--------------+-----------+-----------+-------+
| Chromosome   | Start     | End       | +6    |
| (category)   | (int64)   | (int64)   | ...   |
|--------------+-----------+-----------+-------|
| chr18        | 19791932  | 19791933  | ...   |
| chr18        | 19791935  | 19791936  | ...   |
| chr18        | 19791935  | 19791936  | ...   |
| chr18        | 19791936  | 19791937  | ...   |
| ...          | ...       | ...       | ...   |
| chr18        | 23931941  | 23931942  | ...   |
| chr18        | 23931944  | 23931945  | ...   |
| chr18        | 23932275  | 23932276  | ...   |
| chr18        | 23932294  | 23932295  | ...   |
+--------------+-----------+-----------+-------+
Unstranded PyRanges object has 51,700 rows and 9 columns from 1 chromosomes.
For printing, the PyRanges was sorted on Chromosome.
6 hidden columns: ID, Ref, Alt, Qual, Filter, Info

# Read GTF file as reference data

In [5]:
gtf_path = "/s/genomes/Gencode/Gencode_human/release_40/gencode.v40.annotation.gtf.gz"
gtf = pr.read_gtf(gtf_path)
gtf

+--------------+------------+------------+-----------+-----------+-------+
| Chromosome   | Source     | Feature    | Start     | End       | +20   |
| (category)   | (object)   | (object)   | (int64)   | (int64)   | ...   |
|--------------+------------+------------+-----------+-----------+-------|
| chr1         | HAVANA     | exon       | 11868     | 12227     | ...   |
| chr1         | HAVANA     | gene       | 11868     | 14409     | ...   |
| chr1         | HAVANA     | transcript | 11868     | 14409     | ...   |
| chr1         | HAVANA     | exon       | 12009     | 12057     | ...   |
| ...          | ...        | ...        | ...       | ...       | ...   |
| chrY         | HAVANA     | exon       | 57213203  | 57213357  | ...   |
| chrY         | HAVANA     | exon       | 57213525  | 57213602  | ...   |
| chrY         | HAVANA     | exon       | 57213879  | 57213964  | ...   |
| chrY         | HAVANA     | exon       | 57214349  | 57214397  | ...   |
+--------------+------------+------------+-----------+-----------+-------+
Stranded PyRanges object has 3,283,862 rows and 25 columns from 25 chromosomes.
For printing, the PyRanges was sorted on Chromosome and Strand.
20 hidden columns: Score, Strand, Frame, gene_id, transcript_id, gene_type, gene_name, ... (+ 13 more.)

## Filter GTF

In [6]:
cds = gtf[gtf.Feature == "CDS"] 
transcripts = gtf[gtf.Feature == "transcript"]
exons = gtf[gtf.Feature == "exon"]  # wir müssen nach exons filtern

In [7]:
exons_df = exons.df

# add exon length here (for long exon rule)
exons_df["exon_length"] = exons_df["End"] - exons_df["Start"]

exons_df = exons_df[exons_df["Chromosome"].isin(["chr18"])]
exons_df

Chromosome  Source Feature     Start       End Score Strand Frame  \
1316984      chr18  HAVANA    exon     11102     11595     .      +     .   
1316985      chr18  HAVANA    exon     11124     11595     .      +     .   
1316986      chr18  HAVANA    exon     13151     13354     .      +     .   
1316987      chr18  HAVANA    exon     15616     15822     .      +     .   
1316988      chr18  HAVANA    exon     15616     16352     .      +     .   
...            ...     ...     ...       ...       ...   ...    ...   ...   
1344782      chr18  HAVANA    exon  80202709  80202881     .      -     .   
1344783      chr18  HAVANA    exon  80202709  80202932     .      -     .   
1344784      chr18  HAVANA    exon  80202709  80202932     .      -     .   
1344785      chr18  HAVANA    exon  80247276  80247348     .      -     .   
1344786      chr18  HAVANA    exon  80247276  80247514     .      -     .   

                    gene_id      transcript_id       gene_type  gene_name  \
1316984   ENSG00000262352.2  ENST00000575820.1          lncRNA  LINC02564   
1316985   ENSG00000262352.2  ENST00000572573.2          lncRNA  LINC02564   
1316986   ENSG00000262352.2  ENST00000572573.2          lncRNA  LINC02564   
1316987   ENSG00000262352.2  ENST00000575820.1          lncRNA  LINC02564   
1316988   ENSG00000262352.2  ENST00000572573.2          lncRNA  LINC02564   
...                     ...                ...             ...        ...   
1344782  ENSG00000178184.16  ENST00000463384.1  protein_coding     PARD6G   
1344783  ENSG00000178184.16  ENST00000353265.8  protein_coding     PARD6G   
1344784  ENSG00000178184.16  ENST00000470488.2  protein_coding     PARD6G   
1344785  ENSG00000178184.16  ENST00000470488.2  protein_coding     PARD6G   
1344786  ENSG00000178184.16  ENST00000353265.8  protein_coding     PARD6G   

        transcript_type transcript_name exon_number            exon_id level  \
1316984          lncRNA   LINC02564-202           1  ENSE00002675641.1     2   
1316985          lncRNA   LINC02564-201           1  ENSE00002655585.2     2   
1316986          lncRNA   LINC02564-201           2  ENSE00002638761.1     2   
1316987          lncRNA   LINC02564-202           2  ENSE00002640309.1     2   
1316988          lncRNA   LINC02564-201           3  ENSE00002652936.2     2   
...                 ...             ...         ...                ...   ...   
1344782  protein_coding      PARD6G-202           1  ENSE00001835352.1     2   
1344783  protein_coding      PARD6G-201           2  ENSE00001273029.1     2   
1344784  protein_coding      PARD6G-203           2  ENSE00001273029.1     1   
1344785  protein_coding      PARD6G-203           1  ENSE00002736871.1     1   
1344786  protein_coding      PARD6G-201           1  ENSE00001941099.2     2   

        transcript_support_level     hgnc_id           tag  \
1316984                        5  HGNC:53604           NaN   
1316985                        3  HGNC:53604        TAGENE   
1316986                        3  HGNC:53604        TAGENE   
1316987                        5  HGNC:53604           NaN   
1316988                        3  HGNC:53604        TAGENE   
...                          ...         ...           ...   
1344782                        3  HGNC:16076  cds_start_NF   
1344783                        1  HGNC:16076          CCDS   
1344784                        1  HGNC:16076      exp_conf   
1344785                        1  HGNC:16076      exp_conf   
1344786                        1  HGNC:16076          CCDS   

                  havana_gene     havana_transcript  ont         protein_id  \
1316984  OTTHUMG00000177910.2  OTTHUMT00000439668.1  NaN                NaN   
1316985  OTTHUMG00000177910.2  OTTHUMT00000439669.2  NaN                NaN   
1316986  OTTHUMG00000177910.2  OTTHUMT00000439669.2  NaN                NaN   
1316987  OTTHUMG00000177910.2  OTTHUMT00000439668.1  NaN                NaN   
1316988  OTTHUMG00000177910.2  OTTHUMT00000439669.2  NaN 

In [8]:
transcripts_df = transcripts.df
transcripts_df = transcripts_df[transcripts_df["Chromosome"].isin(["chr18"])]
transcripts_df

Chromosome  Source     Feature     Start       End Score Strand Frame  \
204531      chr18  HAVANA  transcript     11102     15822     .      +     .   
204532      chr18  HAVANA  transcript     11124     16352     .      +     .   
204533      chr18  HAVANA  transcript     45033     46047     .      +     .   
204534      chr18  HAVANA  transcript    109064    122219     .      +     .   
204535      chr18  HAVANA  transcript    111612    122335     .      +     .   
...           ...     ...         ...       ...       ...   ...    ...   ...   
209272      chr18  HAVANA  transcript  79977601  79988537     .      -     .   
209273      chr18  HAVANA  transcript  79994942  80033894     .      -     .   
209274      chr18  HAVANA  transcript  80157231  80247514     .      -     .   
209275      chr18  HAVANA  transcript  80182849  80247348     .      -     .   
209276      chr18  HAVANA  transcript  80182855  80202881     .      -     .   

                   gene_id      transcript_id  \
204531   ENSG00000262352.2  ENST00000575820.1   
204532   ENSG00000262352.2  ENST00000572573.2   
204533   ENSG00000262181.2  ENST00000575066.2   
204534   ENSG00000263006.7  ENST00000608049.5   
204535   ENSG00000263006.7  ENST00000693583.1   
...                    ...                ...   
209272  ENSG00000141759.15  ENST00000586295.1   
209273  ENSG00000141759.15  ENST00000589926.1   
209274  ENSG00000178184.16  ENST00000353265.8   
209275  ENSG00000178184.16  ENST00000470488.2   
209276  ENSG00000178184.16  ENST00000463384.1   

                                 gene_type        gene_name  \
204531                              lncRNA        LINC02564   
204532                              lncRNA        LINC02564   
204533              unprocessed_pseudogene  ENSG00000262181   
204534  transcribed_unprocessed_pseudogene          ROCK1P1   
204535  transcribed_unprocessed_pseudogene          ROCK1P1   
...                                    ...              ...   
209272                      protein_coding           TXNL4A   
209273                      protein_coding           TXNL4A   
209274                      protein_coding           PARD6G   
209275                      protein_coding           PARD6G   
209276                      protein_coding           PARD6G   

                transcript_type  transcript_name exon_number exon_id level  \
204531                   lncRNA    LINC02564-202         NaN     NaN     2   
204532                   lncRNA    LINC02564-201         NaN     NaN     2   
204533   unprocessed_pseudogene  ENST00000575066         NaN     NaN     2   
204534     processed_transcript      ROCK1P1-203         NaN     NaN     2   
204535     processed_transcript      ROCK1P1-204         NaN     NaN     2   
...                         ...              ...         ...     ...   ...   
209272  nonsense_mediated_decay       TXNL4A-205         NaN     NaN     2   
209273     processed_transcript       TXNL4A-209         NaN     NaN     2   
209274           protein_coding       PARD6G-201         NaN     NaN     2   
209275           protein_coding       PARD6G-203         NaN     NaN     1   
209276           protein_coding       PARD6G-202         NaN     NaN     2   

       transcript_support_level     hgnc_id                     tag  \
204531                        5  HGNC:53604                     NaN   
204532                        3  HGNC:53604                  TAGENE   
204533                       NA         NaN       Ensembl_canonical   
204534                        1  HGNC:37832                   basic   
204535                      NaN  HGNC:37832  RNA_Seq_supported_only   
...                         ...         ...                     ...   
209272                        3  HGNC:30551                     NaN   
209273                        4  HGNC:30551                     NaN   
209274                        1  HGNC:16076                    CCDS   
209275                        1  HGNC:16076          

In [9]:
# Group by transcript_id and count: get number of exons per transcript
exon_counts = exons_df.groupby("transcript_id").size().reset_index(name="num_exons_per_transcript")
exon_counts

# exon_counts["num_exons_per_transcript"].unique()

transcript_id  num_exons_per_transcript
0      ENST00000019317.8                        10
1     ENST00000075430.11                        12
2     ENST00000169551.11                         6
3     ENST00000217515.11                         8
4      ENST00000217652.8                         4
...                  ...                       ...
4741   ENST00000696485.1                        44
4742   ENST00000696489.1                        44
4743   ENST00000696490.1                        43
4744   ENST00000696491.1                         2
4745   ENST00000696785.1                         1

[4746 rows x 2 columns]

In [10]:
filtered_df_with_counts = exons_df.merge(exon_counts, on="transcript_id", how="left")
filtered_df_with_counts["num_exons_per_transcript"] = filtered_df_with_counts["num_exons_per_transcript"].fillna(0).astype(int)
filtered_df_with_counts

Chromosome  Source Feature     Start       End Score Strand Frame  \
0          chr18  HAVANA    exon     11102     11595     .      +     .   
1          chr18  HAVANA    exon     11124     11595     .      +     .   
2          chr18  HAVANA    exon     13151     13354     .      +     .   
3          chr18  HAVANA    exon     15616     15822     .      +     .   
4          chr18  HAVANA    exon     15616     16352     .      +     .   
...          ...     ...     ...       ...       ...   ...    ...   ...   
27798      chr18  HAVANA    exon  80202709  80202881     .      -     .   
27799      chr18  HAVANA    exon  80202709  80202932     .      -     .   
27800      chr18  HAVANA    exon  80202709  80202932     .      -     .   
27801      chr18  HAVANA    exon  80247276  80247348     .      -     .   
27802      chr18  HAVANA    exon  80247276  80247514     .      -     .   

                  gene_id      transcript_id       gene_type  gene_name  \
0       ENSG00000262352.2  ENST00000575820.1          lncRNA  LINC02564   
1       ENSG00000262352.2  ENST00000572573.2          lncRNA  LINC02564   
2       ENSG00000262352.2  ENST00000572573.2          lncRNA  LINC02564   
3       ENSG00000262352.2  ENST00000575820.1          lncRNA  LINC02564   
4       ENSG00000262352.2  ENST00000572573.2          lncRNA  LINC02564   
...                   ...                ...             ...        ...   
27798  ENSG00000178184.16  ENST00000463384.1  protein_coding     PARD6G   
27799  ENSG00000178184.16  ENST00000353265.8  protein_coding     PARD6G   
27800  ENSG00000178184.16  ENST00000470488.2  protein_coding     PARD6G   
27801  ENSG00000178184.16  ENST00000470488.2  protein_coding     PARD6G   
27802  ENSG00000178184.16  ENST00000353265.8  protein_coding     PARD6G   

      transcript_type transcript_name exon_number            exon_id level  \
0              lncRNA   LINC02564-202           1  ENSE00002675641.1     2   
1              lncRNA   LINC02564-201           1  ENSE00002655585.2     2   
2              lncRNA   LINC02564-201           2  ENSE00002638761.1     2   
3              lncRNA   LINC02564-202           2  ENSE00002640309.1     2   
4              lncRNA   LINC02564-201           3  ENSE00002652936.2     2   
...               ...             ...         ...                ...   ...   
27798  protein_coding      PARD6G-202           1  ENSE00001835352.1     2   
27799  protein_coding      PARD6G-201           2  ENSE00001273029.1     2   
27800  protein_coding      PARD6G-203           2  ENSE00001273029.1     1   
27801  protein_coding      PARD6G-203           1  ENSE00002736871.1     1   
27802  protein_coding      PARD6G-201           1  ENSE00001941099.2     2   

      transcript_support_level     hgnc_id           tag  \
0                            5  HGNC:53604           NaN   
1                            3  HGNC:53604        TAGENE   
2                            3  HGNC:53604        TAGENE   
3                            5  HGNC:53604           NaN   
4                            3  HGNC:53604        TAGENE   
...                        ...         ...           ...   
27798                        3  HGNC:16076  cds_start_NF   
27799                        1  HGNC:16076          CCDS   
27800                        1  HGNC:16076      exp_conf   
27801                        1  HGNC:16076      exp_conf   
27802                        1  HGNC:16076          CCDS   

                havana_gene     havana_transcript  ont         protein_id  \
0      OTTHUMG00000177910.2  OTTHUMT00000439668.1  NaN                NaN   
1      OTTHUMG00000177910.2  OTTHUMT00000439669.2  NaN                NaN   
2      OTTHUMG00000177910.2  OTTHUMT00000439669.2  NaN                NaN   
3      OTTHUMG00000177910.2  OTTHUMT00000439668.1  NaN                NaN   
4      OTTHUMG00000177910.2  OTTHUMT00000439669.2  NaN                NaN   
...                     ...                   ...  ...                ...   
27798  

In [11]:
np.sort(exon_counts["num_exons_per_transcript"].unique()) == np.sort(filtered_df_with_counts["num_exons_per_transcript"].unique())

array([ True,  True,  True,  True,  True,  True,  True,  True,  True,
        True,  True,  True,  True,  True,  True,  True,  True,  True,
        True,  True,  True,  True,  True,  True,  True,  True,  True,
        True,  True,  True,  True,  True,  True,  True,  True,  True,
        True,  True,  True,  True,  True,  True,  True,  True,  True,
        True,  True,  True,  True,  True,  True,  True,  True,  True,
        True,  True,  True])

# Read FASTA file

In [12]:
fasta_path = "/s/genomes/Gencode/Gencode_human/release_40/GRCh38.p13.genome.fa"
fasta = Fasta(fasta_path)

In [13]:
# print(f">chr1\n{fasta['chr1'][:100000]}")  # the first 10.000 bases are all N, after that the sequence appears
print(f">chr18\n{fasta['chr18'][19791932:19791933]}") 

>chr18
A


# Implement the rules

Take one Transcript and calculate the features based on this

Exons auf Transcript oder CDS??

Features:
- 50 bp upstream of last exon-exon junction (PTCs <50 nt upstream of the last exon-exon junction) --> im vorletzten exon schauen ob das PTC weniger als 50nt vom Ende entfernt ist)
- Last exon
- Long exon (>= 400nt)
- Start-proximal (PTCs <150bp / <100bp from the start codon)
- Single exon

für PTCs:
- coding sequence berechnen
- dann schauen wo ist das Stop Codon
- normales stop codon ist am ende der coding sequence, wenn das stop codon nicht am ende ist, dann ist es ein PTC


In [14]:
# 1. nach exons filtern
# 2. eine variante mit dem exons intersection --> range intersection
# auf transcript id groupby, dann sortieren und zählen 
# schauen wie ich die exon number herausfinde (exon number = reihenfolge der exons auf dem Transcript)
# exon schauen ob auf plus oder minus strang
# regeln aufzeichnen und schauen --> 1 transcript variante nehmen als Beispiel und schauen 

# - strang ganz am ende reverse kompliment von der Fasta sequenz

## Single exon rule

In [15]:
# Add a column for the single exon NMD rule
filtered_df_with_counts["NMD_is_single_exon"] = filtered_df_with_counts["num_exons_per_transcript"] == 1
filtered_df_with_counts.NMD_is_single_exon.value_counts()

NMD_is_single_exon
False    27146
True       657
Name: count, dtype: int64

## Long exon rule (>= 400nt)

In [16]:
filtered_df_with_counts["NMD_is_long_exon"] = filtered_df_with_counts["exon_length"] >= 400
filtered_df_with_counts

Chromosome  Source Feature     Start       End Score Strand Frame  \
0          chr18  HAVANA    exon     11102     11595     .      +     .   
1          chr18  HAVANA    exon     11124     11595     .      +     .   
2          chr18  HAVANA    exon     13151     13354     .      +     .   
3          chr18  HAVANA    exon     15616     15822     .      +     .   
4          chr18  HAVANA    exon     15616     16352     .      +     .   
...          ...     ...     ...       ...       ...   ...    ...   ...   
27798      chr18  HAVANA    exon  80202709  80202881     .      -     .   
27799      chr18  HAVANA    exon  80202709  80202932     .      -     .   
27800      chr18  HAVANA    exon  80202709  80202932     .      -     .   
27801      chr18  HAVANA    exon  80247276  80247348     .      -     .   
27802      chr18  HAVANA    exon  80247276  80247514     .      -     .   

                  gene_id      transcript_id       gene_type  gene_name  \
0       ENSG00000262352.2  ENST00000575820.1          lncRNA  LINC02564   
1       ENSG00000262352.2  ENST00000572573.2          lncRNA  LINC02564   
2       ENSG00000262352.2  ENST00000572573.2          lncRNA  LINC02564   
3       ENSG00000262352.2  ENST00000575820.1          lncRNA  LINC02564   
4       ENSG00000262352.2  ENST00000572573.2          lncRNA  LINC02564   
...                   ...                ...             ...        ...   
27798  ENSG00000178184.16  ENST00000463384.1  protein_coding     PARD6G   
27799  ENSG00000178184.16  ENST00000353265.8  protein_coding     PARD6G   
27800  ENSG00000178184.16  ENST00000470488.2  protein_coding     PARD6G   
27801  ENSG00000178184.16  ENST00000470488.2  protein_coding     PARD6G   
27802  ENSG00000178184.16  ENST00000353265.8  protein_coding     PARD6G   

      transcript_type transcript_name exon_number            exon_id level  \
0              lncRNA   LINC02564-202           1  ENSE00002675641.1     2   
1              lncRNA   LINC02564-201           1  ENSE00002655585.2     2   
2              lncRNA   LINC02564-201           2  ENSE00002638761.1     2   
3              lncRNA   LINC02564-202           2  ENSE00002640309.1     2   
4              lncRNA   LINC02564-201           3  ENSE00002652936.2     2   
...               ...             ...         ...                ...   ...   
27798  protein_coding      PARD6G-202           1  ENSE00001835352.1     2   
27799  protein_coding      PARD6G-201           2  ENSE00001273029.1     2   
27800  protein_coding      PARD6G-203           2  ENSE00001273029.1     1   
27801  protein_coding      PARD6G-203           1  ENSE00002736871.1     1   
27802  protein_coding      PARD6G-201           1  ENSE00001941099.2     2   

      transcript_support_level     hgnc_id           tag  \
0                            5  HGNC:53604           NaN   
1                            3  HGNC:53604        TAGENE   
2                            3  HGNC:53604        TAGENE   
3                            5  HGNC:53604           NaN   
4                            3  HGNC:53604        TAGENE   
...                        ...         ...           ...   
27798                        3  HGNC:16076  cds_start_NF   
27799                        1  HGNC:16076          CCDS   
27800                        1  HGNC:16076      exp_conf   
27801                        1  HGNC:16076      exp_conf   
27802                        1  HGNC:16076          CCDS   

                havana_gene     havana_transcript  ont         protein_id  \
0      OTTHUMG00000177910.2  OTTHUMT00000439668.1  NaN                NaN   
1      OTTHUMG00000177910.2  OTTHUMT00000439669.2  NaN                NaN   
2      OTTHUMG00000177910.2  OTTHUMT00000439669.2  NaN                NaN   
3      OTTHUMG00000177910.2  OTTHUMT00000439668.1  NaN                NaN   
4      OTTHUMG00000177910.2  OTTHUMT00000439669.2  NaN                NaN   
...                     ...                   ...  ...                ...   
27798  

## Last exon rule

In [17]:
# Ensure exon_number is numeric
filtered_df_with_counts["exon_number"] = pd.to_numeric(filtered_df_with_counts["exon_number"], errors="coerce")

# Compute the max exon number per transcript
max_exon = filtered_df_with_counts.groupby("transcript_id")["exon_number"].transform("max")

# Mark whether the exon is the last one
filtered_df_with_counts["NMD_is_last_exon"] = filtered_df_with_counts["exon_number"] == max_exon
filtered_df_with_counts

Chromosome  Source Feature     Start       End Score Strand Frame  \
0          chr18  HAVANA    exon     11102     11595     .      +     .   
1          chr18  HAVANA    exon     11124     11595     .      +     .   
2          chr18  HAVANA    exon     13151     13354     .      +     .   
3          chr18  HAVANA    exon     15616     15822     .      +     .   
4          chr18  HAVANA    exon     15616     16352     .      +     .   
...          ...     ...     ...       ...       ...   ...    ...   ...   
27798      chr18  HAVANA    exon  80202709  80202881     .      -     .   
27799      chr18  HAVANA    exon  80202709  80202932     .      -     .   
27800      chr18  HAVANA    exon  80202709  80202932     .      -     .   
27801      chr18  HAVANA    exon  80247276  80247348     .      -     .   
27802      chr18  HAVANA    exon  80247276  80247514     .      -     .   

                  gene_id      transcript_id       gene_type  gene_name  \
0       ENSG00000262352.2  ENST00000575820.1          lncRNA  LINC02564   
1       ENSG00000262352.2  ENST00000572573.2          lncRNA  LINC02564   
2       ENSG00000262352.2  ENST00000572573.2          lncRNA  LINC02564   
3       ENSG00000262352.2  ENST00000575820.1          lncRNA  LINC02564   
4       ENSG00000262352.2  ENST00000572573.2          lncRNA  LINC02564   
...                   ...                ...             ...        ...   
27798  ENSG00000178184.16  ENST00000463384.1  protein_coding     PARD6G   
27799  ENSG00000178184.16  ENST00000353265.8  protein_coding     PARD6G   
27800  ENSG00000178184.16  ENST00000470488.2  protein_coding     PARD6G   
27801  ENSG00000178184.16  ENST00000470488.2  protein_coding     PARD6G   
27802  ENSG00000178184.16  ENST00000353265.8  protein_coding     PARD6G   

      transcript_type transcript_name  exon_number            exon_id level  \
0              lncRNA   LINC02564-202            1  ENSE00002675641.1     2   
1              lncRNA   LINC02564-201            1  ENSE00002655585.2     2   
2              lncRNA   LINC02564-201            2  ENSE00002638761.1     2   
3              lncRNA   LINC02564-202            2  ENSE00002640309.1     2   
4              lncRNA   LINC02564-201            3  ENSE00002652936.2     2   
...               ...             ...          ...                ...   ...   
27798  protein_coding      PARD6G-202            1  ENSE00001835352.1     2   
27799  protein_coding      PARD6G-201            2  ENSE00001273029.1     2   
27800  protein_coding      PARD6G-203            2  ENSE00001273029.1     1   
27801  protein_coding      PARD6G-203            1  ENSE00002736871.1     1   
27802  protein_coding      PARD6G-201            1  ENSE00001941099.2     2   

      transcript_support_level     hgnc_id           tag  \
0                            5  HGNC:53604           NaN   
1                            3  HGNC:53604        TAGENE   
2                            3  HGNC:53604        TAGENE   
3                            5  HGNC:53604           NaN   
4                            3  HGNC:53604        TAGENE   
...                        ...         ...           ...   
27798                        3  HGNC:16076  cds_start_NF   
27799                        1  HGNC:16076          CCDS   
27800                        1  HGNC:16076      exp_conf   
27801                        1  HGNC:16076      exp_conf   
27802                        1  HGNC:16076          CCDS   

                havana_gene     havana_transcript  ont         protein_id  \
0      OTTHUMG00000177910.2  OTTHUMT00000439668.1  NaN                NaN   
1      OTTHUMG00000177910.2  OTTHUMT00000439669.2  NaN                NaN   
2      OTTHUMG00000177910.2  OTTHUMT00000439669.2  NaN                NaN   
3      OTTHUMG00000177910.2  OTTHUMT00000439668.1  NaN                NaN   
4      OTTHUMG00000177910.2  OTTHUMT00000439669.2  NaN                NaN   
...                     ...                   ...  ...                ..

In [18]:
(filtered_df_with_counts["NMD_is_single_exon"] == filtered_df_with_counts["NMD_is_last_exon"]).all()

np.False_

# extract PTCs

50 bp upstream of last exon-exon junction (PTCs <50 nt upstream of the last exon-exon junction) --> im vorletzten exon schauen ob das PTC weniger als 50nt vom Ende entfernt ist)

Start-proximal (PTCs <150bp / <100bp from the start codon)

1. CDS vom Transcript berechnen (aus FASTA)
2. dann schauen wo ist das Stop Codon: original Stop Codon (am Ende der CDS) und neues Stop Codon (liegt vor dem originalen Stop Codon)
3. Will die Position vom PTC im Exon wissen
4. Will die Nummer des Exons wissen (z.B. vorletztes)

Note: 
- Ich kann die Varianten skippen die keine PTC generieren
- für den minus Strang ganz am ende das reverse kompliment von der Fasta sequenz nehmen

In [19]:
# Lets start with the following dataset
filtered_df_with_counts

Chromosome  Source Feature     Start       End Score Strand Frame  \
0          chr18  HAVANA    exon     11102     11595     .      +     .   
1          chr18  HAVANA    exon     11124     11595     .      +     .   
2          chr18  HAVANA    exon     13151     13354     .      +     .   
3          chr18  HAVANA    exon     15616     15822     .      +     .   
4          chr18  HAVANA    exon     15616     16352     .      +     .   
...          ...     ...     ...       ...       ...   ...    ...   ...   
27798      chr18  HAVANA    exon  80202709  80202881     .      -     .   
27799      chr18  HAVANA    exon  80202709  80202932     .      -     .   
27800      chr18  HAVANA    exon  80202709  80202932     .      -     .   
27801      chr18  HAVANA    exon  80247276  80247348     .      -     .   
27802      chr18  HAVANA    exon  80247276  80247514     .      -     .   

                  gene_id      transcript_id       gene_type  gene_name  \
0       ENSG00000262352.2  ENST00000575820.1          lncRNA  LINC02564   
1       ENSG00000262352.2  ENST00000572573.2          lncRNA  LINC02564   
2       ENSG00000262352.2  ENST00000572573.2          lncRNA  LINC02564   
3       ENSG00000262352.2  ENST00000575820.1          lncRNA  LINC02564   
4       ENSG00000262352.2  ENST00000572573.2          lncRNA  LINC02564   
...                   ...                ...             ...        ...   
27798  ENSG00000178184.16  ENST00000463384.1  protein_coding     PARD6G   
27799  ENSG00000178184.16  ENST00000353265.8  protein_coding     PARD6G   
27800  ENSG00000178184.16  ENST00000470488.2  protein_coding     PARD6G   
27801  ENSG00000178184.16  ENST00000470488.2  protein_coding     PARD6G   
27802  ENSG00000178184.16  ENST00000353265.8  protein_coding     PARD6G   

      transcript_type transcript_name  exon_number            exon_id level  \
0              lncRNA   LINC02564-202            1  ENSE00002675641.1     2   
1              lncRNA   LINC02564-201            1  ENSE00002655585.2     2   
2              lncRNA   LINC02564-201            2  ENSE00002638761.1     2   
3              lncRNA   LINC02564-202            2  ENSE00002640309.1     2   
4              lncRNA   LINC02564-201            3  ENSE00002652936.2     2   
...               ...             ...          ...                ...   ...   
27798  protein_coding      PARD6G-202            1  ENSE00001835352.1     2   
27799  protein_coding      PARD6G-201            2  ENSE00001273029.1     2   
27800  protein_coding      PARD6G-203            2  ENSE00001273029.1     1   
27801  protein_coding      PARD6G-203            1  ENSE00002736871.1     1   
27802  protein_coding      PARD6G-201            1  ENSE00001941099.2     2   

      transcript_support_level     hgnc_id           tag  \
0                            5  HGNC:53604           NaN   
1                            3  HGNC:53604        TAGENE   
2                            3  HGNC:53604        TAGENE   
3                            5  HGNC:53604           NaN   
4                            3  HGNC:53604        TAGENE   
...                        ...         ...           ...   
27798                        3  HGNC:16076  cds_start_NF   
27799                        1  HGNC:16076          CCDS   
27800                        1  HGNC:16076      exp_conf   
27801                        1  HGNC:16076      exp_conf   
27802                        1  HGNC:16076          CCDS   

                havana_gene     havana_transcript  ont         protein_id  \
0      OTTHUMG00000177910.2  OTTHUMT00000439668.1  NaN                NaN   
1      OTTHUMG00000177910.2  OTTHUMT00000439669.2  NaN                NaN   
2      OTTHUMG00000177910.2  OTTHUMT00000439669.2  NaN                NaN   
3      OTTHUMG00000177910.2  OTTHUMT00000439668.1  NaN                NaN   
4      OTTHUMG00000177910.2  OTTHUMT00000439669.2  NaN                NaN   
...                     ...                   ...  ...                ..

In [20]:
# 1. get CDS of the transcript we are looking at (using GTF file and Feature = CDS)
cds_df = cds.df
cds_df = cds_df[cds_df["Chromosome"].isin(["chr18"])]
cds_df # filtered_cds before

Chromosome  Source Feature     Start       End Score Strand Frame  \
710821      chr18  HAVANA     CDS    158698    158714     .      +     0   
710822      chr18  HAVANA     CDS    158698    158714     .      +     0   
710823      chr18  HAVANA     CDS    158698    158714     .      +     0   
710824      chr18  HAVANA     CDS    158698    158714     .      +     0   
710825      chr18  HAVANA     CDS    163307    163453     .      +     2   
...           ...     ...     ...       ...       ...   ...    ...   ...   
725325      chr18  HAVANA     CDS  80202709  80202881     .      -     0   
725326      chr18  HAVANA     CDS  80202709  80202932     .      -     0   
725327      chr18  HAVANA     CDS  80202709  80202932     .      -     0   
725328      chr18  HAVANA     CDS  80247276  80247348     .      -     0   
725329      chr18  HAVANA     CDS  80247276  80247348     .      -     0   

                   gene_id      transcript_id       gene_type gene_name  \
710821  ENSG00000101557.15  ENST00000261601.8  protein_coding     USP14   
710822  ENSG00000101557.15  ENST00000383589.6  protein_coding     USP14   
710823  ENSG00000101557.15  ENST00000400266.7  protein_coding     USP14   
710824  ENSG00000101557.15  ENST00000582707.5  protein_coding     USP14   
710825  ENSG00000101557.15  ENST00000261601.8  protein_coding     USP14   
...                    ...                ...             ...       ...   
725325  ENSG00000178184.16  ENST00000463384.1  protein_coding    PARD6G   
725326  ENSG00000178184.16  ENST00000353265.8  protein_coding    PARD6G   
725327  ENSG00000178184.16  ENST00000470488.2  protein_coding    PARD6G   
725328  ENSG00000178184.16  ENST00000353265.8  protein_coding    PARD6G   
725329  ENSG00000178184.16  ENST00000470488.2  protein_coding    PARD6G   

       transcript_type transcript_name exon_number            exon_id level  \
710821  protein_coding       USP14-201           1  ENSE00002691455.2     2   
710822  protein_coding       USP14-202           1  ENSE00002693806.1     2   
710823  protein_coding       USP14-203           1  ENSE00001542200.3     2   
710824  protein_coding       USP14-208           1  ENSE00001208684.6     2   
710825  protein_coding       USP14-201           2  ENSE00003682471.1     2   
...                ...             ...         ...                ...   ...   
725325  protein_coding      PARD6G-202           1  ENSE00001835352.1     2   
725326  protein_coding      PARD6G-201           2  ENSE00001273029.1     2   
725327  protein_coding      PARD6G-203           2  ENSE00001273029.1     1   
725328  protein_coding      PARD6G-201           1  ENSE00001941099.2     2   
725329  protein_coding      PARD6G-203           1  ENSE00002736871.1     1   

       transcript_support_level     hgnc_id           tag  \
710821                        1  HGNC:12612          CCDS   
710822                        5  HGNC:12612         basic   
710823                        2  HGNC:12612         basic   
710824                        5  HGNC:12612          CCDS   
710825                        1  HGNC:12612          CCDS   
...                         ...         ...           ...   
725325                        3  HGNC:16076  cds_start_NF   
725326                        1  HGNC:16076          CCDS   
725327                        1  HGNC:16076      exp_conf   
725328                        1  HGNC:16076          CCDS   
725329                        1  HGNC:16076      exp_conf   

                  havana_gene     havana_transcript  ont         protein_id  \
710821  OTTHUMG00000178040.10  OTTHUMT00000440305.4  NaN  ENSP00000261601.6   
710822  OTTHUMG00000178040.10  OTTHUMT00000440307.1  NaN  ENSP00000373083.2   
710823  OTTHUMG00000178040.10  OTTHUMT00000440232.1  NaN  ENSP00000383125.3   
710824  OTTHUMG00000178040.10  OTTHUMT00000440319.3  NaN  ENSP00000464447.1   
710825  OTTHUMG00000178040.10  OTTHUMT00000440305.4  NaN  ENSP00000261601.6   
...                       ...        

In [21]:
transcripts_df # filtered for chr18

Chromosome  Source     Feature     Start       End Score Strand Frame  \
204531      chr18  HAVANA  transcript     11102     15822     .      +     .   
204532      chr18  HAVANA  transcript     11124     16352     .      +     .   
204533      chr18  HAVANA  transcript     45033     46047     .      +     .   
204534      chr18  HAVANA  transcript    109064    122219     .      +     .   
204535      chr18  HAVANA  transcript    111612    122335     .      +     .   
...           ...     ...         ...       ...       ...   ...    ...   ...   
209272      chr18  HAVANA  transcript  79977601  79988537     .      -     .   
209273      chr18  HAVANA  transcript  79994942  80033894     .      -     .   
209274      chr18  HAVANA  transcript  80157231  80247514     .      -     .   
209275      chr18  HAVANA  transcript  80182849  80247348     .      -     .   
209276      chr18  HAVANA  transcript  80182855  80202881     .      -     .   

                   gene_id      transcript_id  \
204531   ENSG00000262352.2  ENST00000575820.1   
204532   ENSG00000262352.2  ENST00000572573.2   
204533   ENSG00000262181.2  ENST00000575066.2   
204534   ENSG00000263006.7  ENST00000608049.5   
204535   ENSG00000263006.7  ENST00000693583.1   
...                    ...                ...   
209272  ENSG00000141759.15  ENST00000586295.1   
209273  ENSG00000141759.15  ENST00000589926.1   
209274  ENSG00000178184.16  ENST00000353265.8   
209275  ENSG00000178184.16  ENST00000470488.2   
209276  ENSG00000178184.16  ENST00000463384.1   

                                 gene_type        gene_name  \
204531                              lncRNA        LINC02564   
204532                              lncRNA        LINC02564   
204533              unprocessed_pseudogene  ENSG00000262181   
204534  transcribed_unprocessed_pseudogene          ROCK1P1   
204535  transcribed_unprocessed_pseudogene          ROCK1P1   
...                                    ...              ...   
209272                      protein_coding           TXNL4A   
209273                      protein_coding           TXNL4A   
209274                      protein_coding           PARD6G   
209275                      protein_coding           PARD6G   
209276                      protein_coding           PARD6G   

                transcript_type  transcript_name exon_number exon_id level  \
204531                   lncRNA    LINC02564-202         NaN     NaN     2   
204532                   lncRNA    LINC02564-201         NaN     NaN     2   
204533   unprocessed_pseudogene  ENST00000575066         NaN     NaN     2   
204534     processed_transcript      ROCK1P1-203         NaN     NaN     2   
204535     processed_transcript      ROCK1P1-204         NaN     NaN     2   
...                         ...              ...         ...     ...   ...   
209272  nonsense_mediated_decay       TXNL4A-205         NaN     NaN     2   
209273     processed_transcript       TXNL4A-209         NaN     NaN     2   
209274           protein_coding       PARD6G-201         NaN     NaN     2   
209275           protein_coding       PARD6G-203         NaN     NaN     1   
209276           protein_coding       PARD6G-202         NaN     NaN     2   

       transcript_support_level     hgnc_id                     tag  \
204531                        5  HGNC:53604                     NaN   
204532                        3  HGNC:53604                  TAGENE   
204533                       NA         NaN       Ensembl_canonical   
204534                        1  HGNC:37832                   basic   
204535                      NaN  HGNC:37832  RNA_Seq_supported_only   
...                         ...         ...                     ...   
209272                        3  HGNC:30551                     NaN   
209273                        4  HGNC:30551                     NaN   
209274                        1  HGNC:16076                    CCDS   
209275                        1  HGNC:16076          

In [22]:
intersection = transcripts.join(hg38_example, how=None, suffix="_variant")
intersection

+--------------+------------+------------+-----------+-----------+-------+
| Chromosome   | Source     | Feature    | Start     | End       | +28   |
| (category)   | (object)   | (object)   | (int64)   | (int64)   | ...   |
|--------------+------------+------------+-----------+-----------+-------|
| chr18        | HAVANA     | transcript | 21242231  | 21526112  | ...   |
| chr18        | HAVANA     | transcript | 21242231  | 21526112  | ...   |
| chr18        | HAVANA     | transcript | 21242231  | 21526112  | ...   |
| chr18        | HAVANA     | transcript | 21242231  | 21526112  | ...   |
| ...          | ...        | ...        | ...       | ...       | ...   |
| chr18        | HAVANA     | transcript | 23709824  | 23710287  | ...   |
| chr18        | HAVANA     | transcript | 23709824  | 23710287  | ...   |
| chr18        | HAVANA     | transcript | 23709824  | 23710287  | ...   |
| chr18        | HAVANA     | transcript | 23709824  | 23710287  | ...   |
+--------------+------------+------------+-----------+-----------+-------+
Stranded PyRanges object has 84,977 rows and 33 columns from 1 chromosomes.
For printing, the PyRanges was sorted on Chromosome and Strand.
28 hidden columns: Score, Strand, Frame, gene_id, transcript_id, gene_type, gene_name, ... (+ 21 more.)

In [23]:
# Convert to DataFrame
df = intersection.df

# Drop duplicates to get one strand per transcript_id
transcript_strands = df[["transcript_id", "Strand"]].drop_duplicates()

# Optionally, convert to a dictionary: {transcript_id: strand}
transcript_strand_dict = dict(zip(transcript_strands["transcript_id"], transcript_strands["Strand"]))
transcript_strand_dict

{'ENST00000424526.7': '+',
 'ENST00000584446.5': '+',
 'ENST00000579454.2': '+',
 'ENST00000269218.10': '+',
 'ENST00000584331.1': '+',
 'ENST00000580732.6': '+',
 'ENST00000578368.5': '+',
 'ENST00000581327.1': '+',
 'ENST00000580683.1': '+',
 'ENST00000578955.1': '+',
 'ENST00000578383.1': '+',
 'ENST00000580384.1': '+',
 'ENST00000579618.1': '+',
 'ENST00000300413.10': '+',
 'ENST00000582475.1': '+',
 'ENST00000577906.1': '+',
 'ENST00000578583.1': '+',
 'ENST00000408566.1': '+',
 'ENST00000578646.5': '+',
 'ENST00000261537.7': '+',
 'ENST00000469988.3': '+',
 'ENST00000577749.5': '+',
 'ENST00000578260.1': '+',
 'ENST00000695486.1': '+',
 'ENST00000695487.1': '+',
 'ENST00000516516.1': '+',
 'ENST00000584898.1': '+',
 'ENST00000585185.1': '+',
 'ENST00000584028.1': '+',
 'ENST00000579830.1': '+',
 'ENST00000269216.10': '+',
 'ENST00000581694.1': '+',
 'ENST00000578741.1': '+',
 'ENST00000495480.1': '+',
 'ENST00000384100.1': '+',
 'ENST00000583700.5': '+',
 'ENST00000579124.5': '+'

In [24]:
#cds_df_test = cds_df[cds_df["transcript_id"].isin(["ENST00000019317.8", "ENST00000217515.11"])]
cds_df_test = cds_df[cds_df["transcript_id"].isin(["ENST00000300413.10", "ENST00000592179.6", "ENST00000391403.4", "ENST00000400473.6"])] # 2 examples for both strands
cds_df_test

Chromosome  Source Feature     Start       End Score Strand Frame  \
712650      chr18  HAVANA     CDS  21612429  21612443     .      +     0   
712652      chr18  HAVANA     CDS  21622724  21622801     .      +     1   
712654      chr18  HAVANA     CDS  21623747  21623939     .      +     2   
712657      chr18  HAVANA     CDS  21629061  21629135     .      +     2   
712816      chr18  HAVANA     CDS  23194511  23194540     .      +     0   
712820      chr18  HAVANA     CDS  23213976  23214054     .      +     1   
712825      chr18  HAVANA     CDS  23234607  23234704     .      +     1   
712828      chr18  HAVANA     CDS  23235894  23236051     .      +     0   
712831      chr18  HAVANA     CDS  23237141  23237245     .      +     2   
712835      chr18  HAVANA     CDS  23252959  23253066     .      +     0   
712838      chr18  HAVANA     CDS  23253728  23253936     .      +     1   
712841      chr18  HAVANA     CDS  23257226  23257364     .      +     0   
719607      chr18  HAVANA     CDS  22415576  22417811     .      -     0   
719744      chr18  HAVANA     CDS  23601228  23601309     .      -     0   
719747      chr18  HAVANA     CDS  23612091  23612190     .      -     0   
719750      chr18  HAVANA     CDS  23617731  23617827     .      -     0   
719753      chr18  HAVANA     CDS  23619530  23619629     .      -     0   
719757      chr18  HAVANA     CDS  23629852  23629951     .      -     0   
719760      chr18  HAVANA     CDS  23634050  23634149     .      -     0   
719762      chr18  HAVANA     CDS  23638848  23638947     .      -     0   
719765      chr18  HAVANA     CDS  23646188  23646287     .      -     0   
719769      chr18  HAVANA     CDS  23649082  23649193     .      -     0   
719773      chr18  HAVANA     CDS  23662709  23662730     .      -     0   

                   gene_id       transcript_id       gene_type gene_name  \
712650  ENSG00000167088.11  ENST00000300413.10  protein_coding    SNRPD1   
712652  ENSG00000167088.11  ENST00000300413.10  protein_coding    SNRPD1   
712654  ENSG00000167088.11  ENST00000300413.10  protein_coding    SNRPD1   
712657  ENSG00000167088.11  ENST00000300413.10  protein_coding    SNRPD1   
712816  ENSG00000134508.13   ENST00000400473.6  protein_coding   CABLES1   
712820  ENSG00000134508.13   ENST00000400473.6  protein_coding   CABLES1   
712825  ENSG00000134508.13   ENST00000400473.6  protein_coding   CABLES1   
712828  ENSG00000134508.13   ENST00000400473.6  protein_coding   CABLES1   
712831  ENSG00000134508.13   ENST00000400473.6  protein_coding   CABLES1   
712835  ENSG00000134508.13   ENST00000400473.6  protein_coding   CABLES1   
712838  ENSG00000134508.13   ENST00000400473.6  protein_coding   CABLES1   
712841  ENSG00000134508.13   ENST00000400473.6  protein_coding   CABLES1   
719607   ENSG00000212710.5   ENST00000391403.4  protein_coding    CTAGE1   
719744  ENSG00000154065.17   ENST00000592179.6  protein_coding   ANKRD29   
719747  ENSG00000154065.17   ENST00000592179.6  protein_coding   ANKRD29   
719750  ENSG00000154065.17   ENST00000592179.6  protein_coding   ANKRD29   
719753  ENSG00000154065.17   ENST00000592179.6  protein_coding   ANKRD29   
719757  ENSG00000154065.17   ENST00000592179.6  protein_coding   ANKRD29   
719760  ENSG00000154065.17   ENST00000592179.6  protein_coding   ANKRD29   
719762  ENSG00000154065.17   ENST00000592179.6  protein_coding   ANKRD29   
719765  ENSG00000154065.17   ENST00000592179.6  protein_coding   ANKRD29   
719769  ENSG00000154065.17   ENST00000592179.6  protein_coding   ANKRD29   
719773  ENSG00000154065.17   ENST00000592179.6  protein_coding   ANKRD29   

       transcript_type transcript_name exon_number            exon_id level  \
712650  protein_coding      SNRPD1-201           1  ENSE00001137497.5     2   
712652  protein_coding      SNRPD1-201           2  ENSE00001109516.1     2   
712654  protein_coding      SNRPD1-201           3  ENSE00003666946.1     2   
712657  protein_coding      SNRPD1-201   

In [25]:
# We need to adjust the positions, because the stop codon is not in the sequence

def adjust_last_cds_for_stop_codon(df, exon_col="exon_number", transcript_col="transcript_id"):
    df = df.copy()
    
    # Search for the last exon in a transcript
    df[exon_col] = df[exon_col].astype(int) # because otherwise e.g. 10 smaller than 9
    df.sort_values(by=[transcript_col, exon_col], inplace=True)
    last_exon_idx = df.groupby(transcript_col)[exon_col].idxmax()

    # Adjust start or end based on strand
    for idx in last_exon_idx:
        strand = df.at[idx, "Strand"]
        if strand == "+":
            df.at[idx, "End"] += 3
        elif strand == "-":
            df.at[idx, "Start"] -= 3
    
    return df

cds_df_test = adjust_last_cds_for_stop_codon(cds_df_test)
cds_df_test

Chromosome  Source Feature     Start       End Score Strand Frame  \
712650      chr18  HAVANA     CDS  21612429  21612443     .      +     0   
712652      chr18  HAVANA     CDS  21622724  21622801     .      +     1   
712654      chr18  HAVANA     CDS  21623747  21623939     .      +     2   
712657      chr18  HAVANA     CDS  21629061  21629138     .      +     2   
719607      chr18  HAVANA     CDS  22415573  22417811     .      -     0   
712816      chr18  HAVANA     CDS  23194511  23194540     .      +     0   
712820      chr18  HAVANA     CDS  23213976  23214054     .      +     1   
712825      chr18  HAVANA     CDS  23234607  23234704     .      +     1   
712828      chr18  HAVANA     CDS  23235894  23236051     .      +     0   
712831      chr18  HAVANA     CDS  23237141  23237245     .      +     2   
712835      chr18  HAVANA     CDS  23252959  23253066     .      +     0   
712838      chr18  HAVANA     CDS  23253728  23253936     .      +     1   
712841      chr18  HAVANA     CDS  23257226  23257367     .      +     0   
719773      chr18  HAVANA     CDS  23662709  23662730     .      -     0   
719769      chr18  HAVANA     CDS  23649082  23649193     .      -     0   
719765      chr18  HAVANA     CDS  23646188  23646287     .      -     0   
719762      chr18  HAVANA     CDS  23638848  23638947     .      -     0   
719760      chr18  HAVANA     CDS  23634050  23634149     .      -     0   
719757      chr18  HAVANA     CDS  23629852  23629951     .      -     0   
719753      chr18  HAVANA     CDS  23619530  23619629     .      -     0   
719750      chr18  HAVANA     CDS  23617731  23617827     .      -     0   
719747      chr18  HAVANA     CDS  23612091  23612190     .      -     0   
719744      chr18  HAVANA     CDS  23601225  23601309     .      -     0   

                   gene_id       transcript_id       gene_type gene_name  \
712650  ENSG00000167088.11  ENST00000300413.10  protein_coding    SNRPD1   
712652  ENSG00000167088.11  ENST00000300413.10  protein_coding    SNRPD1   
712654  ENSG00000167088.11  ENST00000300413.10  protein_coding    SNRPD1   
712657  ENSG00000167088.11  ENST00000300413.10  protein_coding    SNRPD1   
719607   ENSG00000212710.5   ENST00000391403.4  protein_coding    CTAGE1   
712816  ENSG00000134508.13   ENST00000400473.6  protein_coding   CABLES1   
712820  ENSG00000134508.13   ENST00000400473.6  protein_coding   CABLES1   
712825  ENSG00000134508.13   ENST00000400473.6  protein_coding   CABLES1   
712828  ENSG00000134508.13   ENST00000400473.6  protein_coding   CABLES1   
712831  ENSG00000134508.13   ENST00000400473.6  protein_coding   CABLES1   
712835  ENSG00000134508.13   ENST00000400473.6  protein_coding   CABLES1   
712838  ENSG00000134508.13   ENST00000400473.6  protein_coding   CABLES1   
712841  ENSG00000134508.13   ENST00000400473.6  protein_coding   CABLES1   
719773  ENSG00000154065.17   ENST00000592179.6  protein_coding   ANKRD29   
719769  ENSG00000154065.17   ENST00000592179.6  protein_coding   ANKRD29   
719765  ENSG00000154065.17   ENST00000592179.6  protein_coding   ANKRD29   
719762  ENSG00000154065.17   ENST00000592179.6  protein_coding   ANKRD29   
719760  ENSG00000154065.17   ENST00000592179.6  protein_coding   ANKRD29   
719757  ENSG00000154065.17   ENST00000592179.6  protein_coding   ANKRD29   
719753  ENSG00000154065.17   ENST00000592179.6  protein_coding   ANKRD29   
719750  ENSG00000154065.17   ENST00000592179.6  protein_coding   ANKRD29   
719747  ENSG00000154065.17   ENST00000592179.6  protein_coding   ANKRD29   
719744  ENSG00000154065.17   ENST00000592179.6  protein_coding   ANKRD29   

       transcript_type transcript_name  exon_number            exon_id level  \
712650  protein_coding      SNRPD1-201            1  ENSE00001137497.5     2   
712652  protein_coding      SNRPD1-201            2  ENSE00001109516.1     2   
712654  protein_coding      SNRPD1-201            3  ENSE00003666946.1     2   
712657  protein_coding      SNRPD1-20

In [25]:
print(f">chr18\n{fasta['chr18'][23601225:23601309]}")

>chr18
TTAGCTCTTTCTGGGACCTTCTTTACTTCTCAGGAGACGCAATATACGTTCATTTTTGGTTAGTTCTGCCGGAAGTTCATTGGC


In [24]:
for index, row in intersection.df.query("transcript_type == 'protein_coding'").iterrows(): # später hier die Transkripte filtern die ich rausgesucht habe

    chromosome = row["Chromosome"]
    variant_start = row["Start_variant"]
    variant_end = row["End_variant"]
    Ref = row["Ref"]
    Alt = row["Alt"]
    transcript_id = row["transcript_id"]
    
    variant = pr.PyRanges(chromosomes=[chromosome], starts=[variant_start], ends=[variant_end])
    transcript_cds = cds_df[cds_df["transcript_id"] == row["transcript_id"]]

    joined_df = pr.PyRanges(transcript_cds).join(variant, how=None, suffix="_variant")

    if joined_df.empty:
        continue

    break 
    
joined_df

+--------------+------------+------------+-----------+-----------+-------+
| Chromosome   | Source     | Feature    |     Start |       End | +22   |
| (category)   | (object)   | (object)   |   (int64) |   (int64) | ...   |
|--------------+------------+------------+-----------+-----------+-------|
| chr18        | HAVANA     | CDS        |  21383518 |  21383675 | ...   |
+--------------+------------+------------+-----------+-----------+-------+
Stranded PyRanges object has 1 rows and 27 columns from 1 chromosomes.
For printing, the PyRanges was sorted on Chromosome and Strand.
22 hidden columns: Score, Strand, Frame, gene_id, transcript_id, gene_type, gene_name, ... (+ 15 more.)

In [26]:
Ref

'T'

In [27]:
example_cds = transcript_cds.head(1)
example_cds

Chromosome  Source Feature     Start       End Score Strand Frame  \
712519      chr18  HAVANA     CDS  21383518  21383675     .      +     0   

                   gene_id      transcript_id       gene_type gene_name  \
712519  ENSG00000141449.16  ENST00000424526.7  protein_coding    GREB1L   

       transcript_type transcript_name exon_number            exon_id level  \
712519  protein_coding      GREB1L-202           3  ENSE00003694289.1     2   

       transcript_support_level     hgnc_id   tag           havana_gene  \
712519                        5  HGNC:31042  CCDS  OTTHUMG00000178892.3   

       havana_transcript  ont         protein_id       ccdsid  
712519               NaN  NaN  ENSP00000412060.1  CCDS45836.1

In [28]:
print(f">chr18\n{fasta['chr18'][56603026:56603056]}") 

>chr18
TTAGTGGCTTTCTCCTTTTTTGCCAACTAC


In [29]:
example_cds_minus = cds_df_test.iloc[[9]]
example_cds_minus

Chromosome  Source Feature     Start       End Score Strand Frame  \
723498      chr18  HAVANA     CDS  56603029  56603056     .      -     0   

                   gene_id       transcript_id       gene_type gene_name  \
723498  ENSG00000091164.13  ENST00000217515.11  protein_coding     TXNL1   

       transcript_type transcript_name exon_number            exon_id level  \
723498  protein_coding       TXNL1-201           8  ENSE00001106452.4     2   

       transcript_support_level     hgnc_id   tag           havana_gene  \
723498                        1  HGNC:12436  CCDS  OTTHUMG00000132722.7   

           havana_transcript  ont         protein_id       ccdsid  
723498  OTTHUMT00000256064.3  NaN  ENSP00000217515.5  CCDS11961.1

In [30]:
# Create test VCF in create_test_VCF.ipynb, which created the test_variants.vcf

# read in the test variants file
def read_vcf_test(vcf_path):
    df = pd.read_csv(
        vcf_path,
        comment='#',
        sep='\t',
        header=None,
        names=['Chromosome', 'Start', 'ID', 'Ref', 'Alt', 'Qual', 'Filter', 'Info']
    )
    
    # Adjust coordinates
    df['Start'] = df['Start'] # without -1 in the case of our own VCF file --> change later
    df['End'] = df['Start'] + df['Ref'].str.len()
    
    gr = pr.PyRanges(df[['Chromosome', 'Start', 'End', 'ID', 'Ref', 'Alt', 'Qual', 'Filter', 'Info']])
    return gr
    
# test_variants = read_vcf_test("test_variants.vcf")
test_variants = read_vcf_test("test_variants_minus.vcf")
test_variants

+--------------+-----------+-----------+-------+
| Chromosome   | Start     | End       | +6    |
| (category)   | (int64)   | (int64)   | ...   |
|--------------+-----------+-----------+-------|
| chr18        | 56603029  | 56603032  | ...   |
| chr18        | 56603028  | 56603032  | ...   |
| chr18        | 56603028  | 56603031  | ...   |
| chr18        | 56603029  | 56603032  | ...   |
| ...          | ...       | ...       | ...   |
| chr18        | 56603037  | 56603043  | ...   |
| chr18        | 56603053  | 56603059  | ...   |
| chr18        | 56603053  | 56603059  | ...   |
| chr18        | 56603053  | 56603059  | ...   |
+--------------+-----------+-----------+-------+
Unstranded PyRanges object has 22 rows and 9 columns from 1 chromosomes.
For printing, the PyRanges was sorted on Chromosome.
6 hidden columns: ID, Ref, Alt, Qual, Filter, Info

In [26]:
#example_cds = example_cds_minus
#intersection_test = pr.PyRanges(example_cds).join(test_variants, how=None, suffix="_variant").df
#intersection_test

intersection_test = pr.PyRanges(cds_df_test).join(hg38_example, how=None, suffix="_variant").df # test with two transcript example
intersection_test

Chromosome  Source Feature     Start       End Score Strand Frame  \
0       chr18  HAVANA     CDS  21622724  21622801     .      +     1   
1       chr18  HAVANA     CDS  21623747  21623939     .      +     2   
2       chr18  HAVANA     CDS  23194511  23194540     .      +     0   
3       chr18  HAVANA     CDS  23213976  23214054     .      +     1   
4       chr18  HAVANA     CDS  23213976  23214054     .      +     1   
5       chr18  HAVANA     CDS  23253728  23253936     .      +     1   
6       chr18  HAVANA     CDS  23257226  23257367     .      +     0   
7       chr18  HAVANA     CDS  22415573  22417811     .      -     0   
8       chr18  HAVANA     CDS  22415573  22417811     .      -     0   
9       chr18  HAVANA     CDS  22415573  22417811     .      -     0   
10      chr18  HAVANA     CDS  22415573  22417811     .      -     0   
11      chr18  HAVANA     CDS  22415573  22417811     .      -     0   
12      chr18  HAVANA     CDS  22415573  22417811     .      -     0   
13      chr18  HAVANA     CDS  22415573  22417811     .      -     0   
14      chr18  HAVANA     CDS  22415573  22417811     .      -     0   
15      chr18  HAVANA     CDS  22415573  22417811     .      -     0   
16      chr18  HAVANA     CDS  22415573  22417811     .      -     0   
17      chr18  HAVANA     CDS  22415573  22417811     .      -     0   
18      chr18  HAVANA     CDS  22415573  22417811     .      -     0   
19      chr18  HAVANA     CDS  22415573  22417811     .      -     0   
20      chr18  HAVANA     CDS  22415573  22417811     .      -     0   
21      chr18  HAVANA     CDS  22415573  22417811     .      -     0   
22      chr18  HAVANA     CDS  22415573  22417811     .      -     0   
23      chr18  HAVANA     CDS  22415573  22417811     .      -     0   
24      chr18  HAVANA     CDS  22415573  22417811     .      -     0   
25      chr18  HAVANA     CDS  22415573  22417811     .      -     0   
26      chr18  HAVANA     CDS  22415573  22417811     .      -     0   
27      chr18  HAVANA     CDS  22415573  22417811     .      -     0   
28      chr18  HAVANA     CDS  22415573  22417811     .      -     0   
29      chr18  HAVANA     CDS  23649082  23649193     .      -     0   
30      chr18  HAVANA     CDS  23634050  23634149     .      -     0   
31      chr18  HAVANA     CDS  23629852  23629951     .      -     0   
32      chr18  HAVANA     CDS  23619530  23619629     .      -     0   
33      chr18  HAVANA     CDS  23612091  23612190     .      -     0   
34      chr18  HAVANA     CDS  23601225  23601309     .      -     0   

               gene_id       transcript_id       gene_type gene_name  \
0   ENSG00000167088.11  ENST00000300413.10  protein_coding    SNRPD1   
1   ENSG00000167088.11  ENST00000300413.10  protein_coding    SNRPD1   
2   ENSG00000134508.13   ENST00000400473.6  protein_coding   CABLES1   
3   ENSG00000134508.13   ENST00000400473.6  protein_coding   CABLES1   
4   ENSG00000134508.13   ENST00000400473.6  protein_coding   CABLES1   
5   ENSG00000134508.13   ENST00000400473.6  protein_coding   CABLES1   
6   ENSG00000134508.13   ENST00000400473.6  protein_coding   CABLES1   
7    ENSG00000212710.5   ENST00000391403.4  protein_coding    CTAGE1   
8    ENSG00000212710.5   ENST00000391403.4  protein_coding    CTAGE1   
9    ENSG00000212710.5   ENST00000391403.4  protein_coding    CTAGE1   
10   ENSG00000212710.5   ENST00000391403.4  protein_coding    CTAGE1   
11   ENSG00000212710.5   ENST00000391403.4  protein_coding    CTAGE1   
12   ENSG00000212710.5   ENST00000391403.4  protein_coding    CTAGE1   
13   ENSG00000212710.5   ENST00000391403.4  protein_coding    CTAGE1   
14   ENSG00000212710.5   ENST00000391403.4  protein_coding    CTAGE1   
15   ENSG00000212710.5   ENST00000391403.4  protein_coding    CTAGE1   
16   ENSG00000212710.5   ENST00000391403.4  protein_coding    CTAGE1   
17   ENSG00000212710.5   ENST00000391403.4  protein_coding    CTAGE1   
18   ENSG00000212710.5   ENST00000391403.4

In [27]:
cds_df_test

Chromosome  Source Feature     Start       End Score Strand Frame  \
712650      chr18  HAVANA     CDS  21612429  21612443     .      +     0   
712652      chr18  HAVANA     CDS  21622724  21622801     .      +     1   
712654      chr18  HAVANA     CDS  21623747  21623939     .      +     2   
712657      chr18  HAVANA     CDS  21629061  21629138     .      +     2   
719607      chr18  HAVANA     CDS  22415573  22417811     .      -     0   
712816      chr18  HAVANA     CDS  23194511  23194540     .      +     0   
712820      chr18  HAVANA     CDS  23213976  23214054     .      +     1   
712825      chr18  HAVANA     CDS  23234607  23234704     .      +     1   
712828      chr18  HAVANA     CDS  23235894  23236051     .      +     0   
712831      chr18  HAVANA     CDS  23237141  23237245     .      +     2   
712835      chr18  HAVANA     CDS  23252959  23253066     .      +     0   
712838      chr18  HAVANA     CDS  23253728  23253936     .      +     1   
712841      chr18  HAVANA     CDS  23257226  23257367     .      +     0   
719773      chr18  HAVANA     CDS  23662709  23662730     .      -     0   
719769      chr18  HAVANA     CDS  23649082  23649193     .      -     0   
719765      chr18  HAVANA     CDS  23646188  23646287     .      -     0   
719762      chr18  HAVANA     CDS  23638848  23638947     .      -     0   
719760      chr18  HAVANA     CDS  23634050  23634149     .      -     0   
719757      chr18  HAVANA     CDS  23629852  23629951     .      -     0   
719753      chr18  HAVANA     CDS  23619530  23619629     .      -     0   
719750      chr18  HAVANA     CDS  23617731  23617827     .      -     0   
719747      chr18  HAVANA     CDS  23612091  23612190     .      -     0   
719744      chr18  HAVANA     CDS  23601225  23601309     .      -     0   

                   gene_id       transcript_id       gene_type gene_name  \
712650  ENSG00000167088.11  ENST00000300413.10  protein_coding    SNRPD1   
712652  ENSG00000167088.11  ENST00000300413.10  protein_coding    SNRPD1   
712654  ENSG00000167088.11  ENST00000300413.10  protein_coding    SNRPD1   
712657  ENSG00000167088.11  ENST00000300413.10  protein_coding    SNRPD1   
719607   ENSG00000212710.5   ENST00000391403.4  protein_coding    CTAGE1   
712816  ENSG00000134508.13   ENST00000400473.6  protein_coding   CABLES1   
712820  ENSG00000134508.13   ENST00000400473.6  protein_coding   CABLES1   
712825  ENSG00000134508.13   ENST00000400473.6  protein_coding   CABLES1   
712828  ENSG00000134508.13   ENST00000400473.6  protein_coding   CABLES1   
712831  ENSG00000134508.13   ENST00000400473.6  protein_coding   CABLES1   
712835  ENSG00000134508.13   ENST00000400473.6  protein_coding   CABLES1   
712838  ENSG00000134508.13   ENST00000400473.6  protein_coding   CABLES1   
712841  ENSG00000134508.13   ENST00000400473.6  protein_coding   CABLES1   
719773  ENSG00000154065.17   ENST00000592179.6  protein_coding   ANKRD29   
719769  ENSG00000154065.17   ENST00000592179.6  protein_coding   ANKRD29   
719765  ENSG00000154065.17   ENST00000592179.6  protein_coding   ANKRD29   
719762  ENSG00000154065.17   ENST00000592179.6  protein_coding   ANKRD29   
719760  ENSG00000154065.17   ENST00000592179.6  protein_coding   ANKRD29   
719757  ENSG00000154065.17   ENST00000592179.6  protein_coding   ANKRD29   
719753  ENSG00000154065.17   ENST00000592179.6  protein_coding   ANKRD29   
719750  ENSG00000154065.17   ENST00000592179.6  protein_coding   ANKRD29   
719747  ENSG00000154065.17   ENST00000592179.6  protein_coding   ANKRD29   
719744  ENSG00000154065.17   ENST00000592179.6  protein_coding   ANKRD29   

       transcript_type transcript_name  exon_number            exon_id level  \
712650  protein_coding      SNRPD1-201            1  ENSE00001137497.5     2   
712652  protein_coding      SNRPD1-201            2  ENSE00001109516.1     2   
712654  protein_coding      SNRPD1-201            3  ENSE00003666946.1     2   
712657  protein_coding      SNRPD1-20

In [28]:
# This code works for plus strand

# Create the CDS and alternative CDS
# TODO: clean up code
# TODO: for minus strand, add reverse complement afterwards?

def apply_variant_edge_aware_with_lengths(row):
    cds_seq = list(row["Exon_CDS_seq"])
    strand = row["Strand"]
    ref = row["Ref"]
    alt = row["Alt"]
    cds_start = int(row["Start"])
    cds_end = int(row["End"])
    var_start = int(row["Start_variant"])
    var_end = int(row["End_variant"])

    # Overlap of the variant with the CDS
    overlap_start = max(var_start, cds_start)
    overlap_end = min(var_end, cds_end)

    if overlap_start >= overlap_end:
        return pd.Series({
            "Exon_CDS_length": len(cds_seq),
            "Exon_Alt_CDS_seq": None,
            "Exon_Alt_CDS_length": None
        })

    cds_index = overlap_start - cds_start
    overlap_len = overlap_end - overlap_start

    # Offset of the overlapping region within the variant
    ref_offset = overlap_start - var_start
    ref_in_cds = ref[ref_offset:ref_offset + overlap_len]
    alt_in_cds = alt[ref_offset:ref_offset + overlap_len]

    # Determine if there’s leftover alt outside CDS (insertions at end)
    extra_alt = ""
    if len(alt) > len(ref):
        # Limit extra_alt to what corresponds to CDS overlap
        extra_start = ref_offset + overlap_len
        if var_end > cds_end:
            # Only include alt bases that map to CDS
            remaining_cds_len = cds_end - overlap_end
            extra_alt = alt[extra_start:extra_start + remaining_cds_len]
        else:
            extra_alt = alt[extra_start:]

    # Confirm that the reference matches
    cds_ref_part = "".join(cds_seq[cds_index:cds_index + overlap_len])
    if cds_ref_part != ref_in_cds.upper():
        return pd.Series({
            "Exon_CDS_length": len(cds_seq),
            "Exon_Alt_CDS_seq": None,
            "Exon_Alt_CDS_length": None
        })

    # Build alternative sequence
    alt_seq = []
    alt_seq.extend(cds_seq[:cds_index]) # Copy the CDS up to the variant position

    if len(ref) == len(alt): # Substitution
        alt_seq.extend(list(alt_in_cds))
    elif len(alt) > len(ref): # Insertion
        alt_seq.extend(list(alt_in_cds))
        alt_seq.extend(list(extra_alt))
    elif len(ref) > len(alt): # Deletion
        alt_seq.extend(list(alt_in_cds))

    # Add the rest of the CDS
    alt_seq.extend(cds_seq[cds_index + overlap_len:])

    return pd.Series({
        "Exon_CDS_length": len(cds_seq),
        "Exon_Alt_CDS_seq": "".join(alt_seq),
        "Exon_Alt_CDS_length": len(alt_seq)
    })

df3 = intersection_test.copy()
df3["Exon_CDS_seq"] = df3.apply(lambda row: fasta[row["Chromosome"]][row["Start"]:row["End"]].seq.upper(), axis=1)

df3[["Exon_CDS_length", "Exon_Alt_CDS_seq", "Exon_Alt_CDS_length"]] = df3.apply(
    apply_variant_edge_aware_with_lengths,
    axis=1
)

df3

Chromosome  Source Feature     Start       End Score Strand Frame  \
0       chr18  HAVANA     CDS  21622724  21622801     .      +     1   
1       chr18  HAVANA     CDS  21623747  21623939     .      +     2   
2       chr18  HAVANA     CDS  23194511  23194540     .      +     0   
3       chr18  HAVANA     CDS  23213976  23214054     .      +     1   
4       chr18  HAVANA     CDS  23213976  23214054     .      +     1   
5       chr18  HAVANA     CDS  23253728  23253936     .      +     1   
6       chr18  HAVANA     CDS  23257226  23257367     .      +     0   
7       chr18  HAVANA     CDS  22415573  22417811     .      -     0   
8       chr18  HAVANA     CDS  22415573  22417811     .      -     0   
9       chr18  HAVANA     CDS  22415573  22417811     .      -     0   
10      chr18  HAVANA     CDS  22415573  22417811     .      -     0   
11      chr18  HAVANA     CDS  22415573  22417811     .      -     0   
12      chr18  HAVANA     CDS  22415573  22417811     .      -     0   
13      chr18  HAVANA     CDS  22415573  22417811     .      -     0   
14      chr18  HAVANA     CDS  22415573  22417811     .      -     0   
15      chr18  HAVANA     CDS  22415573  22417811     .      -     0   
16      chr18  HAVANA     CDS  22415573  22417811     .      -     0   
17      chr18  HAVANA     CDS  22415573  22417811     .      -     0   
18      chr18  HAVANA     CDS  22415573  22417811     .      -     0   
19      chr18  HAVANA     CDS  22415573  22417811     .      -     0   
20      chr18  HAVANA     CDS  22415573  22417811     .      -     0   
21      chr18  HAVANA     CDS  22415573  22417811     .      -     0   
22      chr18  HAVANA     CDS  22415573  22417811     .      -     0   
23      chr18  HAVANA     CDS  22415573  22417811     .      -     0   
24      chr18  HAVANA     CDS  22415573  22417811     .      -     0   
25      chr18  HAVANA     CDS  22415573  22417811     .      -     0   
26      chr18  HAVANA     CDS  22415573  22417811     .      -     0   
27      chr18  HAVANA     CDS  22415573  22417811     .      -     0   
28      chr18  HAVANA     CDS  22415573  22417811     .      -     0   
29      chr18  HAVANA     CDS  23649082  23649193     .      -     0   
30      chr18  HAVANA     CDS  23634050  23634149     .      -     0   
31      chr18  HAVANA     CDS  23629852  23629951     .      -     0   
32      chr18  HAVANA     CDS  23619530  23619629     .      -     0   
33      chr18  HAVANA     CDS  23612091  23612190     .      -     0   
34      chr18  HAVANA     CDS  23601225  23601309     .      -     0   

               gene_id       transcript_id       gene_type gene_name  \
0   ENSG00000167088.11  ENST00000300413.10  protein_coding    SNRPD1   
1   ENSG00000167088.11  ENST00000300413.10  protein_coding    SNRPD1   
2   ENSG00000134508.13   ENST00000400473.6  protein_coding   CABLES1   
3   ENSG00000134508.13   ENST00000400473.6  protein_coding   CABLES1   
4   ENSG00000134508.13   ENST00000400473.6  protein_coding   CABLES1   
5   ENSG00000134508.13   ENST00000400473.6  protein_coding   CABLES1   
6   ENSG00000134508.13   ENST00000400473.6  protein_coding   CABLES1   
7    ENSG00000212710.5   ENST00000391403.4  protein_coding    CTAGE1   
8    ENSG00000212710.5   ENST00000391403.4  protein_coding    CTAGE1   
9    ENSG00000212710.5   ENST00000391403.4  protein_coding    CTAGE1   
10   ENSG00000212710.5   ENST00000391403.4  protein_coding    CTAGE1   
11   ENSG00000212710.5   ENST00000391403.4  protein_coding    CTAGE1   
12   ENSG00000212710.5   ENST00000391403.4  protein_coding    CTAGE1   
13   ENSG00000212710.5   ENST00000391403.4  protein_coding    CTAGE1   
14   ENSG00000212710.5   ENST00000391403.4  protein_coding    CTAGE1   
15   ENSG00000212710.5   ENST00000391403.4  protein_coding    CTAGE1   
16   ENSG00000212710.5   ENST00000391403.4  protein_coding    CTAGE1   
17   ENSG00000212710.5   ENST00000391403.4  protein_coding    CTAGE1   
18   ENSG00000212710.5   ENST00000391403.4

In [ ]:
# Now we have a dataframe with the original CDS sequence, and each row has a different variant
# Need to add that if a row does not have a variant, we still need to compute the CDS for that row, so we can construct the correct CDS and alternative CDS with all combinations

# Maybe we can use the original CDS dataframe: cds_df_test
# df3 has all the variants included but some rows from the cds_df_test are missing since the rows withotu variants get deleted when joining


# 1. Für cds_df_test CDS sequence berechnen ohne Varianten --> done
# 2. cds_df_test nehmen und eine for-loop darauf

In [29]:
# Für cds_df_test CDS sequence berechnen ohne Varianten
# TODO: when to do reverse compliment of minus strand?

cds_df_test["Exon_CDS_seq"] = cds_df_test.apply(lambda row: fasta[row["Chromosome"]][row["Start"]:row["End"]].seq.upper(), axis=1)
cds_df_test

Chromosome  Source Feature     Start       End Score Strand Frame  \
712650      chr18  HAVANA     CDS  21612429  21612443     .      +     0   
712652      chr18  HAVANA     CDS  21622724  21622801     .      +     1   
712654      chr18  HAVANA     CDS  21623747  21623939     .      +     2   
712657      chr18  HAVANA     CDS  21629061  21629138     .      +     2   
719607      chr18  HAVANA     CDS  22415573  22417811     .      -     0   
712816      chr18  HAVANA     CDS  23194511  23194540     .      +     0   
712820      chr18  HAVANA     CDS  23213976  23214054     .      +     1   
712825      chr18  HAVANA     CDS  23234607  23234704     .      +     1   
712828      chr18  HAVANA     CDS  23235894  23236051     .      +     0   
712831      chr18  HAVANA     CDS  23237141  23237245     .      +     2   
712835      chr18  HAVANA     CDS  23252959  23253066     .      +     0   
712838      chr18  HAVANA     CDS  23253728  23253936     .      +     1   
712841      chr18  HAVANA     CDS  23257226  23257367     .      +     0   
719773      chr18  HAVANA     CDS  23662709  23662730     .      -     0   
719769      chr18  HAVANA     CDS  23649082  23649193     .      -     0   
719765      chr18  HAVANA     CDS  23646188  23646287     .      -     0   
719762      chr18  HAVANA     CDS  23638848  23638947     .      -     0   
719760      chr18  HAVANA     CDS  23634050  23634149     .      -     0   
719757      chr18  HAVANA     CDS  23629852  23629951     .      -     0   
719753      chr18  HAVANA     CDS  23619530  23619629     .      -     0   
719750      chr18  HAVANA     CDS  23617731  23617827     .      -     0   
719747      chr18  HAVANA     CDS  23612091  23612190     .      -     0   
719744      chr18  HAVANA     CDS  23601225  23601309     .      -     0   

                   gene_id       transcript_id       gene_type gene_name  \
712650  ENSG00000167088.11  ENST00000300413.10  protein_coding    SNRPD1   
712652  ENSG00000167088.11  ENST00000300413.10  protein_coding    SNRPD1   
712654  ENSG00000167088.11  ENST00000300413.10  protein_coding    SNRPD1   
712657  ENSG00000167088.11  ENST00000300413.10  protein_coding    SNRPD1   
719607   ENSG00000212710.5   ENST00000391403.4  protein_coding    CTAGE1   
712816  ENSG00000134508.13   ENST00000400473.6  protein_coding   CABLES1   
712820  ENSG00000134508.13   ENST00000400473.6  protein_coding   CABLES1   
712825  ENSG00000134508.13   ENST00000400473.6  protein_coding   CABLES1   
712828  ENSG00000134508.13   ENST00000400473.6  protein_coding   CABLES1   
712831  ENSG00000134508.13   ENST00000400473.6  protein_coding   CABLES1   
712835  ENSG00000134508.13   ENST00000400473.6  protein_coding   CABLES1   
712838  ENSG00000134508.13   ENST00000400473.6  protein_coding   CABLES1   
712841  ENSG00000134508.13   ENST00000400473.6  protein_coding   CABLES1   
719773  ENSG00000154065.17   ENST00000592179.6  protein_coding   ANKRD29   
719769  ENSG00000154065.17   ENST00000592179.6  protein_coding   ANKRD29   
719765  ENSG00000154065.17   ENST00000592179.6  protein_coding   ANKRD29   
719762  ENSG00000154065.17   ENST00000592179.6  protein_coding   ANKRD29   
719760  ENSG00000154065.17   ENST00000592179.6  protein_coding   ANKRD29   
719757  ENSG00000154065.17   ENST00000592179.6  protein_coding   ANKRD29   
719753  ENSG00000154065.17   ENST00000592179.6  protein_coding   ANKRD29   
719750  ENSG00000154065.17   ENST00000592179.6  protein_coding   ANKRD29   
719747  ENSG00000154065.17   ENST00000592179.6  protein_coding   ANKRD29   
719744  ENSG00000154065.17   ENST00000592179.6  protein_coding   ANKRD29   

       transcript_type transcript_name  exon_number            exon_id level  \
712650  protein_coding      SNRPD1-201            1  ENSE00001137497.5     2   
712652  protein_coding      SNRPD1-201            2  ENSE00001109516.1     2   
712654  protein_coding      SNRPD1-201            3  ENSE00003666946.1     2   
712657  protein_coding      SNRPD1-20

In [37]:
# TODO: create an example of a Deletion that goes over 2 exons and check if this incorporates it correctly

results = []

for transcript_id, var_df in df3.groupby("transcript_id"):  # Only transcripts with a variant

    # 1. Get reference exons
    ref_exons = cds_df_test[cds_df_test["transcript_id"] == transcript_id].copy()
    ref_exons = ref_exons.sort_values("Start")

    # Join reference sequence
    ref_seq = "".join(ref_exons["Exon_CDS_seq"].tolist())

    # Get strand info (all should be the same within transcript)
    strand = ref_exons["Strand"].iloc[0]

    for variant, cds_df in var_df.groupby(["Chromosome", "Start_variant", "End_variant", "Ref", "Alt"], observed=True):

        # Sort variant exons
        cds_df = cds_df.sort_values("Start")

        # Copy ref exons for modification
        alt_exons = ref_exons.copy()

        # Replace affected exon sequences with variant versions
        for _, var_row in cds_df.iterrows():
            exon_nr = var_row["exon_number"]
            alt_exons.loc[alt_exons["exon_number"] == exon_nr, "Exon_CDS_seq"] = var_row["Exon_Alt_CDS_seq"]

        # Join and sort alt CDS
        alt_exons = alt_exons.sort_values("Start")
        alt_seq = "".join(alt_exons["Exon_CDS_seq"].tolist())

        # Apply reverse complement if on minus strand
        if strand == "-":
            ref_seq_final = str(Seq(ref_seq).reverse_complement())
            alt_seq_final = str(Seq(alt_seq).reverse_complement())
        else:
            ref_seq_final = ref_seq
            alt_seq_final = alt_seq

        # Append to results
        results.append({
            "transcript_id": transcript_id,
            "variant_id": var_row["ID"],
            "ref_seq": ref_seq_final,
            "alt_seq": alt_seq_final,
            "ref_len": len(ref_seq_final),
            "alt_len": len(alt_seq_final),
            "chromosome": var_row["Chromosome"],
            "strand": strand,
            "ref": var_row["Ref"],
            "alt": var_row["Alt"],
            "start_variant": var_row["Start_variant"],
            "end_variant": var_row["End_variant"]
        })

# Convert to DataFrame
results_df = pd.DataFrame(results)
results_df

# df3 so unterteilt, dass ich alle Varianten für ein Transkript have
# -> für dieses eine Transkript kann ich jetzt die ganzen CDS Sequenzen berechnen. D.h. ich muss es nicht bei jeder Variante neu machen weil es unterscheidet sich nicht, die Referenz wid immer gleich sein für das selbe Transkript.
# Für jedes Transkript erstmal die Referenz-Sequenz berechnen aus meinen CDS chunks (nach START sortieren!)

# cds_df_test wo transcript_id = das was ich suche, sortiere nach Start, für Ref-Sequenz hänge ich diese nur zusammen
# für Alt ersetze ich dieses eine cds das von der variante betroffen ist --> ersetze alles was ich im cds_df_test habe durch das cds das von der Variante betroffen ist: cds_df (alle Zeilen) (nach exon_number rauslöschen)

# Ich habe 2 dataframes:
# 1. für Referenz Sequenz wo ich meine X CDS snippets drin habe
# 2. Liste vo Coding sequences die von der Variante betroffen sind (cds_df Spalte exon_number)
# Jetzt geh ich durch die referenz_df durch, lösche alles raus wo cds_df exon_number drin steht und füge die Stellen von cds_df ein für die Alternative Sequenz



transcript_id                    variant_id  \
0   ENST00000300413.10   chr18:21622773:21622774:G>A   
1   ENST00000300413.10   chr18:21623889:21623890:A>G   
2    ENST00000391403.4   chr18:22415689:22415690:C>T   
3    ENST00000391403.4   chr18:22415742:22415743:G>T   
4    ENST00000391403.4   chr18:22415772:22415773:G>A   
5    ENST00000391403.4   chr18:22415781:22415782:G>A   
6    ENST00000391403.4   chr18:22415787:22415788:A>C   
7    ENST00000391403.4   chr18:22415809:22415810:T>A   
8    ENST00000391403.4   chr18:22415809:22415810:T>C   
9    ENST00000391403.4   chr18:22415888:22415889:A>C   
10   ENST00000391403.4   chr18:22415997:22415998:C>T   
11   ENST00000391403.4   chr18:22416009:22416010:G>A   
12   ENST00000391403.4   chr18:22416061:22416062:G>T   
13   ENST00000391403.4   chr18:22416312:22416313:G>A   
14   ENST00000391403.4   chr18:22416317:22416318:A>G   
15   ENST00000391403.4   chr18:22416607:22416608:G>T   
16   ENST00000391403.4   chr18:22416684:22416685:C>T   
17   ENST00000391403.4   chr18:22416758:22416759:T>C   
18   ENST00000391403.4   chr18:22416930:22416931:G>A   
19   ENST00000391403.4   chr18:22416966:22416967:G>T   
20   ENST00000391403.4   chr18:22417450:22417451:C>G   
21   ENST00000391403.4   chr18:22417604:22417605:A>G   
22   ENST00000391403.4   chr18:22417766:22417767:C>G   
23   ENST00000391403.4   chr18:22417802:22417803:G>T   
24   ENST00000400473.6   chr18:23194514:23194515:C>T   
25   ENST00000400473.6   chr18:23214036:23214037:C>T   
26   ENST00000400473.6   chr18:23214049:23214050:G>A   
27   ENST00000400473.6   chr18:23253745:23253746:G>A   
28   ENST00000400473.6   chr18:23257282:23257283:G>A   
29   ENST00000592179.6   chr18:23601292:23601293:G>A   
30   ENST00000592179.6  chr18:23612166:23612167:T>TG   
31   ENST00000592179.6   chr18:23619551:23619552:G>A   
32   ENST00000592179.6   chr18:23629930:23629931:G>A   
33   ENST00000592179.6   chr18:23634145:23634146:C>T   
34   ENST00000592179.6   chr18:23649137:23649138:G>A   

                                              ref_seq  \
0   ATGAAGCTCGTGAGATTTTTGATGAAATTGAGTCATGAAACTGTAA...   
1   ATGAAGCTCGTGAGATTTTTGATGAAATTGAGTCATGAAACTGTAA...   
2   ATGAGACCCGATTCTCATCCTTATGGTTTTCCATGGGAATTGGTGA...   
3   ATGAGACCCGATTCTCATCCTTATGGTTTTCCATGGGAATTGGTGA...   
4   ATGAGACCCGATTCTCATCCTTATGGTTTTCCATGGGAATTGGTGA...   
5   ATGAGACCCGATTCTCATCCTTATGGTTTTCCATGGGAATTGGTGA...   
6   ATGAGACCCGATTCTCATCCTTATGGTTTTCCATGGGAATTGGTGA...   
7   ATGAGACCCGATTCTCATCCTTATGGTTTTCCATGGGAATTGGTGA...   
8   ATGAGACCCGATTCTCATCCTTATGGTTTTCCATGGGAATTGGTGA...   
9   ATGAGACCCGATTCTCATCCTTATGGTTTTCCATGGGAATTGGTGA...   
10  ATGAGACCCGATTCTCATCCTTATGGTTTTCCATGGGAATTGGTGA...   
11  ATGAGACCCGATTCTCATCCTTATGGTTTTCCATGGGAATTGGTGA...   
12  ATGAGACCCGATTCTCATCCTTATGGTTTTCCATGGGAATTGGTGA...   
13  ATGAGACCCGATTCTCATCCTTATGGTTTTCCATGGGAATTGGTGA...   
14  ATGAGACCCGATTCTCATCCTTATGGTTTTCCATGGGAATTGGTGA...   
15  ATGAGACCCGATTCTCATCCTTATGGTTTTCCATGGGAATTGGTGA...   
16  ATGAGACCCGATTCTCATCCTTATGGTTTTCCATGGGAATTGGTGA...   
17  ATGAGACCCGATTCTCATCCTTATGGTTTTCCATGGGAATTGGTGA...   
18  ATGAGACCCGATTCTCATCCTTATGGTTTTCCATGGGAATTGGTGA...   
19  ATGAGACCCGATTCTCATCCTTATGGTTTTCCATGGGAATTGGTGA...   
20  ATGAGACCCGATTCTCATCCTTATGGTTTTCCATGGGAATTGGTGA...   
21  ATGAGACCCGATTCTCATCCTTATGGTTTTCCATGGGAATTGGTGA...   
22  ATGAGACCCGATTCTCATCCTTATGGTTTTCCATGGGAATTGGTGA...   
23  ATGAGACCCGATTCTCATCCTTATGGTTTTCCATGGGAATTGGTGA...   
24  ATGCGGCAACACGATACCAGGAATGGCAGAATAGTCCTTATCAGTG...   
25  ATGCGGCAACACGATACCAGGAATGGCAGAATAGTCCTTATCAGTG...   
26  ATGCGGCAACACGATACCAGGAATGGCAGAATAGTCCTTATCAGTG...   
27  ATGCGGCAACACGATACCAGGAATGGCAGAATAGTCCTTATCAGTG...   
28  ATGCGGCAACACGATACCAGGAATGGCAGAATAGTCCTTATCAGTG...   
29  ATGTGCAGGATGTCCTTCAAGAAGGAAACTCCACTTGCCAATGCTG...   
30  ATGTGCAGGATGTCCTTCAAGAAGGAAACTCCACTTGCCAATGCTG...   
31  ATGTGCAGGATGTCCTTCAAGAAGGAAACTCCACTTGCCAATGCTG...   
32  ATGTGCAGGATGTCCTTCAAGAAGGAAACTCCACTTGCCAATGCTG...   
33  ATGTGCAGGATGTCCTTCAAGAAGGAAACTCCACTTGCCAATGCTG... 

In [63]:
print(f">chr18\n{fasta['chr18'][22417766:22417770]}") 

>chr18
CACC


In [40]:
row = results_df.iloc[30]

print(f"Transcript ID: {row['transcript_id']}")
print(f"Variant ID: {row['variant_id']}\n")

print("Reference CDS (ref_seq):")
print(row["ref_seq"])

print("\nAlternative CDS (alt_seq):")
print(row["alt_seq"])


Transcript ID: ENST00000592179.6
Variant ID: chr18:23612166:23612167:T>TG

Reference CDS (ref_seq):
ATGTGCAGGATGTCCTTCAAGAAGGAAACTCCACTTGCCAATGCTGCATTCTGGGCAGCCAGGAGAGGAAACCTGGCGCTGCTGAAGCTGCTGTTGAACAGCGGCCGGGTGGACGTGGACTGCAGAGACAGCCATGGCACCACACTCCTGATGGTTGCTGCCTACGCTGGCCACATAGACTGTGTGAGGGAACTGGTTCTGCAAGGAGCAGACATCAATCTCCAGAGAGAGTCAGGTACAACTGCCCTATTCTTTGCCGCCCAGCAAGGCCATAATGATGTCGTGAGATTTCTCTTTGGATTTGGAGCATCCACTGAATTTAGGACCAAAGACGGGGGCACCGCCCTGTTGGCTGCCAGTCAGTACGGGCACATGCAGGTGGTGGAGACCTTGCTGAAGCACGGAGCAAACATCCATGACCAACTTTATGATGGAGCCACTGCCCTCTTCCTAGCTGCCCAAGGTGGTTACTTGGATGTTATTCGATTACTGCTGGCTTCAGGAGCAAAAGTCAACCAGCCAAGGCAGGACGGGACAGCGCCCCTGTGGATCGCGTCCCAGATGGGCCACAGCGAGGTGGTGCGGGTGATGCTGCTGCGCGGAGCCGACCGCGACGCTGCGCGGAACGATGGCACAACAGCATTATTGAAAGCAGCCAACAAAGGGTATAATGATGTCATAAAAGAGTTGCTTAAATTCTCACCCACTCTTGGTATTTTGAAGAATGGGACATCAGCGCTCCATGCAGCAGTGCTCAGTGGAAACATTAAAACAGTTGCGCTGCTCCTAGAAGCAGGGGCAGACCCATCCCTGAGAAACAAGGCCAATGAACTTCCGGCAGAACTAACCAAAAATGAACGTATATTGCGTCTCCTGAGAAGTAAAGAAGGTCCCAGAAAG

In [53]:
# Make sure you only print once per transcript_id
for transcript_id, group in results_df.groupby("transcript_id"):
    ref_seq = group["ref_seq"].iloc[0]  # assuming it's the same for all rows in that group
    print(f"Transcript ID: {transcript_id}")
    print(f"Reference CDS sequence:\n{ref_seq}\n{'-'*80}\n")

Transcript ID: ENST00000300413.10
Reference CDS sequence:
ATGAAGCTCGTGAGATTTTTGATGAAATTGAGTCATGAAACTGTAACCATTGAATTGAAGAACGGAACACAGGTCCATGGAACAATCACAGGTGTGGATGTCAGCATGAATACACATCTTAAAGCTGTGAAAATGACCCTGAAGAACAGAGAACCTGTACAGCTGGAAACGCTGAGTATTCGAGGAAATAACATTCGGTATTTTATTCTACCAGACAGTTTACCTCTGGATACACTACTTGTGGATGTTGAACCTAAGGTGAAATCTAAGAAAAGGGAAGCTGTTGCAGGAAGAGGCAGAGGAAGAGGAAGAGGAAGAGGACGTGGCCGTGGCAGAGGAAGAGGGGGTCCTAGGCGATAA
--------------------------------------------------------------------------------

Transcript ID: ENST00000391403.4
Reference CDS sequence:
TCAGAATGTGGGGGCTGGGGGGAAAAATGCAGGTCTTGGGGGACGGTAAGGAAGAAAACCTCTCGGTAAATAGACATTTCTCATTGCAAATGGAGCACGTGGTGGACCTGGGACATCCCTTGGAGAAAAATAATCTGGAGAAGCTCCAAACACGGTTCCTGGAGGAGGTGGGGGGAAAGGAGGTCCTCTTCTTATGAACGGGCCCCTTGTATCTACTGGAAACAATAAACCTCTGATTGGAGCAAGAGGTGGAGGAACAAAGCCAGGGCCAGTTGCTTCATTTTCAGCGGGGAGAGATGAATCAGGCACCTTTAAATTACCAAGATTATCTTTGGTATCATTTCTACTGGATTCCATTTCTGAAGGCATTGACCCATCCATTTTATCCAAAGAAGGCATATTAAAACTTCTGAGTTCTGCTGGTCCAGAGAGTCTAGCACAA

In [43]:
transcript_id

'ENST00000592179.6'

In [37]:
var_df # transcript_seq und alt_transcript_seq berechnen und hinzufügen (nach START Position sortieren zum berechnen)

Chromosome  Source Feature     Start       End Score Strand Frame  \
29      chr18  HAVANA     CDS  23649082  23649193     .      -     0   
30      chr18  HAVANA     CDS  23634050  23634149     .      -     0   
31      chr18  HAVANA     CDS  23629852  23629951     .      -     0   
32      chr18  HAVANA     CDS  23619530  23619629     .      -     0   
33      chr18  HAVANA     CDS  23612091  23612190     .      -     0   
34      chr18  HAVANA     CDS  23601225  23601309     .      -     0   

               gene_id      transcript_id       gene_type gene_name  \
29  ENSG00000154065.17  ENST00000592179.6  protein_coding   ANKRD29   
30  ENSG00000154065.17  ENST00000592179.6  protein_coding   ANKRD29   
31  ENSG00000154065.17  ENST00000592179.6  protein_coding   ANKRD29   
32  ENSG00000154065.17  ENST00000592179.6  protein_coding   ANKRD29   
33  ENSG00000154065.17  ENST00000592179.6  protein_coding   ANKRD29   
34  ENSG00000154065.17  ENST00000592179.6  protein_coding   ANKRD29   

   transcript_type transcript_name  exon_number            exon_id level  \
29  protein_coding     ANKRD29-208            2  ENSE00001730310.1     2   
30  protein_coding     ANKRD29-208            5  ENSE00003528749.1     2   
31  protein_coding     ANKRD29-208            6  ENSE00002295562.1     2   
32  protein_coding     ANKRD29-208            7  ENSE00003610879.1     2   
33  protein_coding     ANKRD29-208            9  ENSE00003580052.1     2   
34  protein_coding     ANKRD29-208           10  ENSE00002939848.1     2   

   transcript_support_level     hgnc_id   tag           havana_gene  \
29                        1  HGNC:27110  CCDS  OTTHUMG00000131875.6   
30                        1  HGNC:27110  CCDS  OTTHUMG00000131875.6   
31                        1  HGNC:27110  CCDS  OTTHUMG00000131875.6   
32                        1  HGNC:27110  CCDS  OTTHUMG00000131875.6   
33                        1  HGNC:27110  CCDS  OTTHUMG00000131875.6   
34                        1  HGNC:27110  CCDS  OTTHUMG00000131875.6   

       havana_transcript  ont         protein_id       ccdsid  Start_variant  \
29  OTTHUMT00000254825.2  NaN  ENSP00000468354.1  CCDS11879.1       23649137   
30  OTTHUMT00000254825.2  NaN  ENSP00000468354.1  CCDS11879.1       23634145   
31  OTTHUMT00000254825.2  NaN  ENSP00000468354.1  CCDS11879.1       23629930   
32  OTTHUMT00000254825.2  NaN  ENSP00000468354.1  CCDS11879.1       23619551   
33  OTTHUMT00000254825.2  NaN  ENSP00000468354.1  CCDS11879.1       23612166   
34  OTTHUMT00000254825.2  NaN  ENSP00000468354.1  CCDS11879.1       23601292   

    End_variant                            ID Ref Alt Qual Filter Info  \
29     23649138   chr18:23649137:23649138:G>A   G   A    .      .    .   
30     23634146   chr18:23634145:23634146:C>T   C   T    .      .    .   
31     23629931   chr18:23629930:23629931:G>A   G   A    .      .    .   
32     23619552   chr18:23619551:23619552:G>A   G   A    .      .    .   
33     23612167  chr18:23612166:23612167:T>TG   T  TG    .      .    .   
34     23601293   chr18:23601292:23601293:G>A   G   A    .      .    .   

                                         Exon_CDS_seq  Exon_CDS_length  \
29  GCTGTCTCTGCAGTCCACGTCCACCCGGCCGCTGTTCAACAGCAGC...              111   
30  ATAAAGTTGGTCATGGATGTTTGCTCCGTGCTTCAGCAAGGTCTCC...               99   
31  CTGCCTTGGCTGGTTGACTTTTGCTCCTGAAGCCAGCAGTAATCGA...               99   
32  GTTCCGCGCAGCGTCGCGGTCGGCTCCGCGCAGCAGCATCACCCGC...               99   
33  CTTGTTTCTCAGGGATGGGTCTGCCCCTGCTTCTAGGAGCAGCGCA...               99   
34  TTAGCTCTTTCTGGGACCTTCTTTACTTCTCAGGAGACGCAATATA...               84   

                                     Exon_Alt_CDS_seq  Exon_Alt_CDS_length  
29  GCTGTCTCTGCAGTCCACGTCCACCCGGCCGCTGTTCAACAGCAGC...                  111  
30  ATAAAGTTGGTCATGGATGTTTGCTCCGTGCTTCAGCAAGGTCTCC...                   99  
31  CTGCCTTGGCTGGTTGACTTTTGCTCCTGAAGCCAGCAGTAATCGA...                   99  
32  GTTCCGCGCAGCGTCGCGGTCAGCTCCGCGCAGCAGCATCACCCGC...         

In [32]:
cds_df

Chromosome  Source Feature     Start       End Score Strand Frame  \
29      chr18  HAVANA     CDS  23649082  23649193     .      -     0   

               gene_id      transcript_id       gene_type gene_name  \
29  ENSG00000154065.17  ENST00000592179.6  protein_coding   ANKRD29   

   transcript_type transcript_name  exon_number            exon_id level  \
29  protein_coding     ANKRD29-208            2  ENSE00001730310.1     2   

   transcript_support_level     hgnc_id   tag           havana_gene  \
29                        1  HGNC:27110  CCDS  OTTHUMG00000131875.6   

       havana_transcript  ont         protein_id       ccdsid  Start_variant  \
29  OTTHUMT00000254825.2  NaN  ENSP00000468354.1  CCDS11879.1       23649137   

    End_variant                           ID Ref Alt Qual Filter Info  \
29     23649138  chr18:23649137:23649138:G>A   G   A    .      .    .   

                                              CDS_seq  CDS_length  \
29  GCTGTCTCTGCAGTCCACGTCCACCCGGCCGCTGTTCAACAGCAGC...         111   

                                          Alt_CDS_seq  Alt_CDS_length  
29  GCTGTCTCTGCAGTCCACGTCCACCCGGCCGCTGTTCAACAGCAGC...             111

In [33]:
variant

('chr18', np.int64(23649137), np.int64(23649138), 'G', 'A')

In [ ]:
# desired Output: pro Variante und Transkript eine Zeile plus Original CDS plus Alternative CDS

In [29]:
merged = df3.merge(cds_df_test, on="transcript_id", suffixes=("_var", "_cds"))
merged.head(30)

Chromosome_var Source_var Feature_var  Start_var   End_var Score_var  \
0           chr18     HAVANA         CDS   21622724  21622801         .   
1           chr18     HAVANA         CDS   21622724  21622801         .   
2           chr18     HAVANA         CDS   21622724  21622801         .   
3           chr18     HAVANA         CDS   21622724  21622801         .   
4           chr18     HAVANA         CDS   21623747  21623939         .   
5           chr18     HAVANA         CDS   21623747  21623939         .   
6           chr18     HAVANA         CDS   21623747  21623939         .   
7           chr18     HAVANA         CDS   21623747  21623939         .   
8           chr18     HAVANA         CDS   23194511  23194540         .   
9           chr18     HAVANA         CDS   23194511  23194540         .   
10          chr18     HAVANA         CDS   23194511  23194540         .   
11          chr18     HAVANA         CDS   23194511  23194540         .   
12          chr18     HAVANA         CDS   23194511  23194540         .   
13          chr18     HAVANA         CDS   23194511  23194540         .   
14          chr18     HAVANA         CDS   23194511  23194540         .   
15          chr18     HAVANA         CDS   23194511  23194540         .   
16          chr18     HAVANA         CDS   23213976  23214054         .   
17          chr18     HAVANA         CDS   23213976  23214054         .   
18          chr18     HAVANA         CDS   23213976  23214054         .   
19          chr18     HAVANA         CDS   23213976  23214054         .   
20          chr18     HAVANA         CDS   23213976  23214054         .   
21          chr18     HAVANA         CDS   23213976  23214054         .   
22          chr18     HAVANA         CDS   23213976  23214054         .   
23          chr18     HAVANA         CDS   23213976  23214054         .   
24          chr18     HAVANA         CDS   23213976  23214054         .   
25          chr18     HAVANA         CDS   23213976  23214054         .   
26          chr18     HAVANA         CDS   23213976  23214054         .   
27          chr18     HAVANA         CDS   23213976  23214054         .   
28          chr18     HAVANA         CDS   23213976  23214054         .   
29          chr18     HAVANA         CDS   23213976  23214054         .   

   Strand_var Frame_var         gene_id_var       transcript_id  \
0           +         1  ENSG00000167088.11  ENST00000300413.10   
1           +         1  ENSG00000167088.11  ENST00000300413.10   
2           +         1  ENSG00000167088.11  ENST00000300413.10   
3           +         1  ENSG00000167088.11  ENST00000300413.10   
4           +         2  ENSG00000167088.11  ENST00000300413.10   
5           +         2  ENSG00000167088.11  ENST00000300413.10   
6           +         2  ENSG00000167088.11  ENST00000300413.10   
7           +         2  ENSG00000167088.11  ENST00000300413.10   
8           +         0  ENSG00000134508.13   ENST00000400473.6   
9           +         0  ENSG00000134508.13   ENST00000400473.6   
10          +         0  ENSG00000134508.13   ENST00000400473.6   
11          +         0  ENSG00000134508.13   ENST00000400473.6   
12          +         0  ENSG00000134508.13   ENST00000400473.6   
13          +         0  ENSG00000134508.13   ENST00000400473.6   
14          +         0  ENSG00000134508.13   ENST00000400473.6   
15          +         0  ENSG00000134508.13   ENST00000400473.6   
16          +         1  ENSG00000134508.13   ENST00000400473.6   
17          +         1  ENSG00000134508.13   ENST00000400473.6   
18          +         1  ENSG00000134508.13   ENST00000400473.6   
19          +         1  ENSG00000134508.13   ENST00000400473.6   
20          +         1  ENSG00000134508.13   ENST00000400473.6   
21          +         1  ENSG00000134508.13   ENST00000400473.6   
22          +         1  ENSG00000134508.13   ENST00000400473.6   
23          +         1  ENSG00000134508.13   ENST00000400473.6   
24

In [ ]:
# Stop Codon is not considered in the positions: add 3, and check on which side for plus and minus strand

In [48]:
valid_stop_codons = {"TAA", "TAG", "TGA"}
start_codon = "ATG"
cds_data = []

for transcript_id, group in cds_df.groupby("transcript_id"):
    strand = group.iloc[0]["Strand"]

    if strand not in ["+", "-"]:
        print(f"Unknown strand for {transcript_id}")
        continue

    # TODO: nach Start sortieren
    group["exon_number"] = group["exon_number"].astype(int) # column exon number is object, convert to int so the following sort works
    group_sorted = group.sort_values(by="exon_number").copy()

    seq_parts = []
    starts = []
    ends = []

    for i, row in group_sorted.iterrows():
        chrom = row["Chromosome"]
        start = int(row["Start"])
        end = int(row["End"])

        # Extend the last exon by +3 on correct end
        if i == group_sorted.index[-1]:
            if strand == "+":
                end += 3
            else:
                start -= 3
                if start < 0:
                    start = 0

        starts.append(start)
        ends.append(end)

        seq = fasta[chrom][start:end].seq
        seq_parts.append(seq)

    # TODO: Variante einbauen, pro variante eine alt seq
        
    if strand == "-":
        revcom_seq_parts = [str(Seq(seq).reverse_complement()) for seq in seq_parts]
        full_seq = "".join(revcom_seq_parts).upper()
    else:
        full_seq = "".join(seq_parts).upper()

    # Codon scanning
    start_pos = None
    stop_codons = []
    for i in range(0, len(full_seq) - 2, 3):
        codon = full_seq[i:i+3]
        if codon == start_codon and start_pos is None:
            start_pos = i
        if codon in valid_stop_codons:
            stop_codons.append((i, codon))

    # Stop codon summary
    last_codon = full_seq[-3:]
    is_valid_stop = last_codon in valid_stop_codons
    first_stop_pos = stop_codons[0][0] if stop_codons else None
    first_stop = stop_codons[0][1] if stop_codons else None
    is_premature = len(stop_codons) > 1 or (stop_codons and stop_codons[0][0] < len(full_seq) - 3)

    # Append all info
    cds_data.append({
        "Chromosome": chrom, 
        "transcript_id": transcript_id,
        "start": min(starts),
        "end": max(ends),
        "strand": strand,
        "cds_sequence": full_seq,
        "cds_length": len(full_seq),
        "start_codon_pos": start_pos,
        "last_codon": last_codon,
        "valid_stop": is_valid_stop,
        "first_stop_codon": first_stop,
        "first_stop_pos": first_stop_pos,
        "num_stop_codons": len(stop_codons),
        "all_stop_codons": stop_codons,
        "is_premature": is_premature
    })

# Create DataFrame
cds_df_CDS = pd.DataFrame(cds_data)

print("No valid stop codon:", (~cds_df_CDS["valid_stop"]).sum())
print("Missing start_codon_pos:", cds_df_CDS["start_codon_pos"].isna().sum())
print("More than 1 stop codon:", (cds_df_CDS["num_stop_codons"] > 1).sum())
print("Missing first_stop_pos:", cds_df_CDS["first_stop_pos"].isna().sum())
print("Mismatch between first_stop_pos and all_stop_codons:", 
      (~(cds_df_CDS["all_stop_codons"].apply(lambda stops: stops[0][0] if stops else None) == cds_df_CDS["first_stop_pos"])).sum()
)

cds_df_CDS

No valid stop codon: 1
Missing start_codon_pos: 1
More than 1 stop codon: 0
Missing first_stop_pos: 1
Mismatch between first_stop_pos and all_stop_codons: 1


Chromosome      transcript_id     start       end strand  \
0      chr18  ENST00000592179.6  23649079  23649193      -   

                                        cds_sequence  cds_length  \
0  AAGGAAACTCCACTTGCCAATGCTGCATTCTGGGCAGCCAGGAGAG...         114   

  start_codon_pos last_codon  valid_stop first_stop_codon first_stop_pos  \
0            None        GTA       False             None           None   

   num_stop_codons all_stop_codons is_premature  
0                0              []           []

In [49]:
cds_df_CDS[cds_df_CDS["transcript_id"] == "ENST00000592179.6"]["cds_sequence"].values[0]

'AAGGAAACTCCACTTGCCAATGCTGCATTCTGGGCAGCCAGGAGAGGAAACCTGGCGCTGCTGAAGCTGCTGTTGAACAGCGGCCGGGTGGACGTGGACTGCAGAGACAGCGTA'

In [25]:
# filter cds_df for only CDS sequences with start codon at position 0 and a valid stop codon.

#cds_df[(cds_df["strand"] == "-") & (cds_df["valid_stop"] == True)]
# cds_df[(cds_df["valid_stop"] == True) & (cds_df["start_codon_pos"] == 0) & (cds_df["num_stop_codons"] == 1 & (cds_df))]

cds_df_CDS_filtered = cds_df_CDS[
    (cds_df_CDS["valid_stop"] == True) &
    (cds_df_CDS["start_codon_pos"] == 0) &
    (cds_df_CDS["num_stop_codons"] == 1) &
    (cds_df_CDS["first_stop_pos"].notna()) &
    (cds_df_CDS["all_stop_codons"].apply(lambda stops: stops[0][0] if stops else None) == cds_df_CDS["first_stop_pos"])
]

cds_df_CDS_filtered

Chromosome       transcript_id     start       end strand  \
0         chr18   ENST00000019317.8   9513045   9535937      +   
1         chr18  ENST00000075430.11  79679947  79753671      +   
2         chr18  ENST00000169551.11  74148808  74158480      +   
3         chr18  ENST00000217515.11  56603026  56638440      -   
4         chr18   ENST00000217652.8   3253247   3255918      +   
...         ...                 ...       ...       ...    ...   
1819      chr18   ENST00000696483.1  45800812  45967239      -   
1820      chr18   ENST00000696484.1  45800853  45967239      -   
1821      chr18   ENST00000696485.1  45882386  45967239      -   
1822      chr18   ENST00000696489.1  45852466  45967239      -   
1823      chr18   ENST00000696490.1  45852642  45967239      -   

                                           cds_sequence  cds_length  \
0     ATGACTGAGTGCTTCCTGCCCCCCACCAGCAGCCCCAGTGAACACC...        1968   
1     ATGGAGGTGCCGGCCGCGGGTCGCGTTCCTGCCGAGGGCGCCCCGA...        2604   
2     ATGATTTGTACTTTTCTACGAGCCGTACAGTATACGGAGAAGCTGC...         747   
3     ATGGTGGGGGTGAAGCCCGTCGGGAGCGACCCGGATTTCCAGCCAG...         870   
4     ATGTCGAGCAAAAGAACAAAGACCAAGACCAAGAAGCGCCCTCAGC...         516   
...                                                 ...         ...   
1819  ATGGCCGAGGCGGTGAAGCCCCAGCGCCGGGCCAAGGCCAAGGCCA...        7635   
1820  ATGGCCGAGGCGGTGAAGCCCCAGCGCCGGGCCAAGGCCAAGGCCA...        7479   
1821  ATGGCCGAGGCGGTGAAGCCCCAGCGCCGGGCCAAGGCCAAGGCCA...        5349   
1822  ATGGCCGAGGCGGTGAAGCCCCAGCGCCGGGCCAAGGCCAAGGCCA...        7737   
1823  ATGGCCGAGGCGGTGAAGCCCCAGCGCCGGGCCAAGGCCAAGGCCA...        7449   

      start_codon_pos last_codon  valid_stop first_stop_codon  first_stop_pos  \
0                 0.0        TGA        True              TGA          1965.0   
1                 0.0        TGA        True              TGA          2601.0   
2                 0.0        TAA        True              TAA           744.0   
3                 0.0        TAA        True              TAA           867.0   
4                 0.0        TGA        True              TGA           513.0   
...               ...        ...         ...              ...             ...   
1819              0.0        TGA        True              TGA          7632.0   
1820              0.0        TAA        True              TAA          7476.0   
1821              0.0        TGA        True              TGA          5346.0   
1822              0.0        TAG        True              TAG          7734.0   
1823              0.0        TGA        True              TGA          7446.0   

      num_stop_codons all_stop_codons is_premature  
0                   1   [(1965, TGA)]        False  
1                   1   [(2601, TGA)]        False  
2                   1    [(744, TAA)]        False  
3                   1    [(867, TAA)]        False  
4                   1    [(513, TGA)]        False  
...               ...             ...          ...  
1819                1   [(7632, TGA)]        False  
1820                1   [(7476, TAA)]        False  
1821                1   [(5346, TGA)]        False  
1822                1   [(7734, TAG)]        False  
1823                1   [(7446, TGA)]        False  

[1189 rows x 15 columns]

In [26]:
# We have the CDS sequence with the start and end position, but we need to consider the gaps in between as well, which can be taken from the GTF filtered by CDS. 
# Meaning if we have e.g. 3 Exons and 3 CDS there might be gaps from the end of one CDS to the start of another because the start and end positions are given relative 
# to the gene / transcript(?). So we need to check for Stop codons on the CDS sequence, and get the position of the stop codon relative to the gene / transcript.

cds_map = {}

for transcript_id, group in cds_df.groupby("transcript_id"):
    strand = group.iloc[0]["Strand"]
    chrom = group.iloc[0]["Chromosome"]
    
    # Sort CDS in transcriptional order
    group_sorted = group.sort_values("Start", ascending=(strand == "+"))
    
    cds_pos = 0  # cumulative CDS position
    exon_mappings = []

    for _, row in group_sorted.iterrows():
        exon_start = int(row["Start"])
        exon_end = int(row["End"])
        exon_len = exon_end - exon_start
        exon_number = int(row["exon_number"])

        exon_mappings.append({
            "genomic_start": exon_start,
            "genomic_end": exon_end,
            "cds_start": cds_pos,
            "cds_end": cds_pos + exon_len,
            "chrom": chrom,
            "strand": strand,
            "exon_number": exon_number
        })

        cds_pos += exon_len

    cds_map[transcript_id] = exon_mappings


cds_map

{'ENST00000019317.8': [{'genomic_start': 9513045,
   'genomic_end': 9513289,
   'cds_start': 0,
   'cds_end': 244,
   'chrom': 'chr18',
   'strand': '+',
   'exon_number': 2},
  {'genomic_start': 9516844,
   'genomic_end': 9517303,
   'cds_start': 244,
   'cds_end': 703,
   'chrom': 'chr18',
   'strand': '+',
   'exon_number': 3},
  {'genomic_start': 9522159,
   'genomic_end': 9522509,
   'cds_start': 703,
   'cds_end': 1053,
   'chrom': 'chr18',
   'strand': '+',
   'exon_number': 4},
  {'genomic_start': 9524593,
   'genomic_end': 9524755,
   'cds_start': 1053,
   'cds_end': 1215,
   'chrom': 'chr18',
   'strand': '+',
   'exon_number': 5},
  {'genomic_start': 9525719,
   'genomic_end': 9525851,
   'cds_start': 1215,
   'cds_end': 1347,
   'chrom': 'chr18',
   'strand': '+',
   'exon_number': 6},
  {'genomic_start': 9530833,
   'genomic_end': 9530941,
   'cds_start': 1347,
   'cds_end': 1455,
   'chrom': 'chr18',
   'strand': '+',
   'exon_number': 7},
  {'genomic_start': 9533334,
   

## create the alternative sequence by incorporating variants from the VCF

In [32]:
# works for + strand, not for minus strand

def get_cds_index(transcript_id, genomic_pos, cds_map):
    """
    Map genomic position to CDS-relative position.
    """
    if transcript_id not in cds_map:
        return None

    for exon in cds_map[transcript_id]:
        start, end = exon["genomic_start"], exon["genomic_end"]
        strand = exon["strand"]
        if start <= genomic_pos < end:
            offset = genomic_pos - start if strand == "+" else end - genomic_pos - 1
            cds_index = exon["cds_start"] + offset
            return cds_index
    return None  # Not in CDS

def apply_variants_to_cds(row, variants_df, cds_map):
    transcript_id = row["transcript_id"]
    strand = row["strand"]
    cds_seq = list(row["cds_sequence"])  # mutable

    variants = variants_df[variants_df["Chromosome"] == row["Chromosome"]]
    modified_seq = cds_seq.copy()

    for _, var in variants.iterrows():
        var_pos = var["Start"]
        ref = var["Ref"]
        alt = var["Alt"]

        if strand == "-":
            ref = str(Seq(ref).reverse_complement())
            alt = str(Seq(alt).reverse_complement())

        cds_index = get_cds_index(transcript_id, var_pos, cds_map)
        
        if cds_index is not None and cds_index < len(cds_seq):

            ref_len = len(ref)
            cds_slice = "".join(cds_seq[cds_index:cds_index + ref_len]).upper()
            
            # check if the ref matches
            if cds_slice != ref.upper():
                context_radius = 2
                context_start = max(0, cds_index - context_radius)
                context_end = min(len(cds_seq), cds_index + context_radius + 1)
                context_seq = "".join(cds_seq[context_start:context_end])
                
                print(
                        f"❤️ [Ref mismatch] Transcript: {transcript_id}, Genomic Pos: {var_pos}, Strand: {strand}, "
                        f"CDS Index: {cds_index}, Expected: {cds_seq[cds_index]}, "
                        f"Found (Ref): {ref}, Context: {context_seq}"
                    )

            else: 
                print(f"💚 [Match] Transcript: {transcript_id}, Genomic Pos: {var_pos}, Strand: {strand}, ")
            
                # create alternative cds here, only when there is a match

            
                
            
            # cds_seq[cds_index] = alt
            
        else:
            # Not within this transcript's CDS
            continue


# Apply variants to each row in cds_df
cds_df_with_alts = cds_df_CDS_filtered.apply(
    lambda row: apply_variants_to_cds(row, variants_df=hg38_example.df, cds_map=cds_map),
    axis=1
)

cds_df_with_alts



💚 [Match] Transcript: ENST00000256925.12, Genomic Pos: 23135927, Strand: +, 
💚 [Match] Transcript: ENST00000256925.12, Genomic Pos: 23135997, Strand: +, 
💚 [Match] Transcript: ENST00000256925.12, Genomic Pos: 23136131, Strand: +, 
💚 [Match] Transcript: ENST00000256925.12, Genomic Pos: 23136186, Strand: +, 
💚 [Match] Transcript: ENST00000256925.12, Genomic Pos: 23136224, Strand: +, 
💚 [Match] Transcript: ENST00000256925.12, Genomic Pos: 23136232, Strand: +, 
💚 [Match] Transcript: ENST00000256925.12, Genomic Pos: 23136508, Strand: +, 
💚 [Match] Transcript: ENST00000256925.12, Genomic Pos: 23136523, Strand: +, 
💚 [Match] Transcript: ENST00000256925.12, Genomic Pos: 23136559, Strand: +, 
💚 [Match] Transcript: ENST00000256925.12, Genomic Pos: 23188894, Strand: +, 
💚 [Match] Transcript: ENST00000256925.12, Genomic Pos: 23194514, Strand: +, 
💚 [Match] Transcript: ENST00000256925.12, Genomic Pos: 23214036, Strand: +, 
💚 [Match] Transcript: ENST00000256925.12, Genomic Pos: 23214049, Strand: +, 

KeyboardInterrupt: 

In [ ]:
    # Reconstruct and reverse complement for minus strand
    alt_seq = "".join(cds_seq)
    
    #if strand == "-":
    #    alt_seq = str(Seq(alt_seq).reverse_complement())

    # Re-scan stop codons
    stop_codons = []
    for i in range(0, len(alt_seq) - 2, 3):
        codon = alt_seq[i:i+3]
        if codon in {"TAA", "TAG", "TGA"}:
            stop_codons.append((i, codon))

    row["cds_sequence_alt"] = alt_seq
    row["gained_stop_codons"] = [
        (pos, codon) for pos, codon in stop_codons if pos < row["cds_length"] - 3 and pos not in [x[0] for x in row["all_stop_codons"]]
    ]
    row["has_ptc_gain"] = len(row["gained_stop_codons"]) > 0

    return row

In [ ]:
print(filtered_cds_df.columns.tolist())

In [ ]:
print(hg38_example.columns.tolist())

In [ ]:
hg38_example

### Test for minus strand since I had some errors:

In [ ]:
cds_df_minus = cds_df_CDS_filtered[cds_df_CDS_filtered["strand"] == "-"]
cds_df_minus

In [ ]:
cds_df_minus[(cds_df_minus["transcript_id"] == "ENST00000678349.1")]

In [ ]:
full_seq = cds_df_minus.loc[
    (cds_df_minus["strand"] == "-") & (cds_df_minus["transcript_id"] == "ENST00000678349.1"),
    "cds_sequence"
].values[0]

ncbi_seq = "ATGGCGCACGCTGGGAGAACAGGGTACGATAACCGGGAGATAGTGATGAAGTACATCCATTATAAGCTGTCGCAGAGGGGCTACGAGTGGGATGCGGGAGATGTGGGCGCCGCGCCCCCGGGGGCCGCCCCCGCACCGGGCATCTTCTCCTCCCAGCCCGGGCACACGCCCCATCCAGCCGCATCCCGGGACCCGGTCGCCAGGACCTCGCCGCTGCAGACCCCGGCTGCCCCCGGCGCCGCCGCGGGGCCTGCGCTCAGCCCGGTGCCACCTGTGGTCCACCTGACCCTCCGCCAGGCCGGCGACGACTTCTCCCGCCGCTACCGCCGCGACTTCGCCGAGATGTCCAGCCAGCTGCACCTGACGCCCTTCACCGCGCGGGGACGCTTTGCCACGGTGGTGGAGGAGCTCTTCAGGGACGGGGTGAACTGGGGGAGGATTGTGGCCTTCTTTGAGTTCGGTGGGGTCATGTGTGTGGAGAGCGTCAACCGGGAGATGTCGCCCCTGGTGGACAACATCGCCCTGTGGATGACTGAGTACCTGAACCGGCACCTGCACACCTGGATCCAGGATAACGGAGGCTGGGTAGGTGCACTTGGTGATGTGAGTCTGGGCTGA"

full_seq == ncbi_seq

In [28]:
from Bio.Seq import Seq

def get_cds_index(transcript_id, genomic_pos, cds_map):
    """
    Map genomic position to CDS-relative position.
    """
    if transcript_id not in cds_map:
        return None

    for exon in cds_map[transcript_id]:
        start, end = exon["genomic_start"], exon["genomic_end"]
        strand = exon["strand"]
        if start <= genomic_pos < end:
            offset = genomic_pos - start if strand == "+" else end - genomic_pos - 1
            cds_index = exon["cds_start"] + offset
            return cds_index
    return None  # Not in CDS

def apply_variants_to_cds(row, variants_df, cds_map):
    transcript_id = row["transcript_id"]
    strand = row["strand"]
    cds_seq = list(row["cds_sequence"])  # mutable

    variants = variants_df[variants_df["Chromosome"] == row["Chromosome"]]
    modified_seq = cds_seq.copy()

    for _, var in variants.iterrows():
        var_pos = var["Start"]
        ref = var["Ref"]
        alt = var["Alt"]

        cds_index = get_cds_index(transcript_id, var_pos, cds_map)
        if cds_index is not None and cds_index < len(cds_seq):

            ref_len = len(ref)
            cds_slice = "".join(cds_seq[cds_index:cds_index + ref_len]).upper()
            
            # Optional: sanity check the ref matches
            if cds_slice != ref.upper():
                context_radius = 2
                context_start = max(0, cds_index - context_radius)
                context_end = min(len(cds_seq), cds_index + context_radius + 1)
                context_seq = "".join(cds_seq[context_start:context_end])
                
                print(
                        f"❤️ [Ref mismatch] Transcript: {transcript_id}, Genomic Pos: {var_pos}, Strand: {strand}, "
                        f"CDS Index: {cds_index}, Expected: {cds_seq[cds_index]}, "
                        f"Found (Ref): {ref}, Context: {context_seq}"
                    )

            else: print(f"💚 [Match] Transcript: {transcript_id}, Genomic Pos: {var_pos}, Strand: {strand}, ")
            
            cds_seq[cds_index] = alt
            
        else:
            # Not within this transcript's CDS
            continue

    # Reconstruct and reverse complement if needed
    alt_seq = "".join(cds_seq)
    if strand == "-":
        alt_seq = str(Seq(alt_seq).reverse_complement())

    # Re-scan stop codons
    stop_codons = []
    for i in range(0, len(alt_seq) - 2, 3):
        codon = alt_seq[i:i+3]
        if codon in {"TAA", "TAG", "TGA"}:
            stop_codons.append((i, codon))

    row["cds_sequence_alt"] = alt_seq
    row["gained_stop_codons"] = [
        (pos, codon) for pos, codon in stop_codons if pos < row["cds_length"] - 3 and pos not in [x[0] for x in row["all_stop_codons"]]
    ]
    row["has_ptc_gain"] = len(row["gained_stop_codons"]) > 0

    return row


# Apply variants to each row in cds_df
cds_df_with_alts = cds_df_minus.apply(
    lambda row: apply_variants_to_cds(row, variants_df=hg38_example.df, cds_map=cds_map),
    axis=1
)

cds_df_with_alts



KeyboardInterrupt: 

In [ ]:
cds_df_with_alts[cds_df_with_alts["strand"] == "+"]

In [ ]:
from Bio.Seq import Seq

def get_cds_index(transcript_id, genomic_pos, cds_map):
    """
    Map genomic position to CDS-relative position.
    """
    if transcript_id not in cds_map:
        return None

    for exon in cds_map[transcript_id]:
        start, end = exon["genomic_start"], exon["genomic_end"]
        strand = exon["strand"]
        if start <= genomic_pos < end:
            offset = genomic_pos - start if strand == "+" else end - genomic_pos - 1
            cds_index = exon["cds_start"] + offset
            return cds_index
    return None  # Not in CDS

def apply_variants_to_cds(row, variants_df, cds_map):
    transcript_id = row["transcript_id"]
    strand = row["strand"]
    cds_seq = list(row["cds_sequence"])  # mutable

    variants = variants_df[variants_df["Chromosome"] == row["Chromosome"]]
    sequence_modified = False

    for _, var in variants.iterrows():
        var_pos = var["Start"]
        ref = var["Ref"]
        alt = var["Alt"]

        cds_index = get_cds_index(transcript_id, var_pos, cds_map)

        if cds_index is None:
            continue  # not in CDS

        # Check if ref sequence matches the expected CDS substring
        ref_len = len(ref)
        if cds_index + ref_len > len(cds_seq):
            continue  # variant would exceed CDS bounds

        # Extract reference slice from CDS
        cds_slice = "".join(cds_seq[cds_index:cds_index + ref_len]).upper()

        if cds_slice != ref.upper():
            context_radius = 5
            context_start = max(0, cds_index - context_radius)
            context_end = min(len(cds_seq), cds_index + ref_len + context_radius)
            context_seq = "".join(cds_seq[context_start:context_end])
            print(
                f"[Ref mismatch] Transcript: {transcript_id}, Genomic Pos: {var_pos}, Strand: {strand}, "
                f"CDS Index: {cds_index}, Expected: {cds_slice}, Found (Ref): {ref}, Context: {context_seq}"
            )
            continue

        # Apply the variant (replacement of 'ref' with 'alt')
        cds_seq[cds_index:cds_index + ref_len] = list(alt)
        sequence_modified = True

    # Reconstruct and reverse complement if needed
    alt_seq = "".join(cds_seq)
    if strand == "-":
        alt_seq = str(Seq(alt_seq).reverse_complement())

    # Find new stop codons
    stop_codons = []
    for i in range(0, len(alt_seq) - 2, 3):
        codon = alt_seq[i:i+3]
        if codon in {"TAA", "TAG", "TGA"}:
            stop_codons.append((i, codon))

    row["cds_sequence_alt"] = alt_seq if sequence_modified else None
    row["gained_stop_codons"] = [
        (pos, codon) for pos, codon in stop_codons
        if pos < row["cds_length"] - 3 and pos not in [x[0] for x in row["all_stop_codons"]]
    ]
    row["has_ptc_gain"] = len(row["gained_stop_codons"]) > 0
    return row

cds_df_with_alts = filtered_cds_df.apply(
    lambda row: apply_variants_to_cds(row, variants_df=hg38_example.df, cds_map=cds_map),
    axis=1
)

cds_df_with_alts

In [121]:
variants_df = hg38_example.df
variants_df

Chromosome     Start       End                             ID  Ref Alt  \
0          chr18  19791932  19791933    chr18:19791932:19791933:A>T    A   T   
1          chr18  19791935  19791936    chr18:19791935:19791936:C>T    C   T   
2          chr18  19791935  19791936    chr18:19791935:19791936:C>A    C   A   
3          chr18  19791936  19791937    chr18:19791936:19791937:G>A    G   A   
4          chr18  19791937  19791938    chr18:19791937:19791938:C>A    C   A   
...          ...       ...       ...                            ...  ...  ..   
51695      chr18  23931641  23931644  chr18:23931641:23931644:CAA>C  CAA   C   
51696      chr18  23931941  23931942    chr18:23931941:23931942:G>A    G   A   
51697      chr18  23931944  23931945    chr18:23931944:23931945:A>G    A   G   
51698      chr18  23932275  23932276    chr18:23932275:23932276:A>G    A   G   
51699      chr18  23932294  23932295    chr18:23932294:23932295:G>A    G   A   

      Qual Filter Info  
0        .      .    .  
1        .      .    .  
2        .      .    .  
3        .      .    .  
4        .      .    .  
...    ...    ...  ...  
51695    .      .    .  
51696    .      .    .  
51697    .      .    .  
51698    .      .    .  
51699    .      .    .  

[51700 rows x 9 columns]

In [ ]:
cds_map

In [ ]:
variants_df

In [ ]:
print(f">chr18\n{fasta['chr18'][19791932:19791933]}") 

In [122]:
from pyfaidx import Fasta

variants_df = hg38_example.df

for idx, row in variants_df.iterrows():
    chrom = row["Chromosome"]
    pos = int(row["Start"])  # VCF is 1-based
    ref = row["Ref"]
    ref_len = len(ref)
    alt = row["Alt"]

    # Normalize chromosome name
    if chrom not in fasta:
        chrom = chrom.replace("chr", "")  # fallback if needed

    if chrom not in fasta:
        print(f"❌ Chromosome {row['Chromosome']} not found in FASTA")
        continue

    # pyfaidx slicing is 1-based and end-inclusive
    fasta_seq = fasta[chrom][pos:pos + ref_len].seq.upper()

    if fasta_seq != ref.upper():
        print(f"⚠️ Ref mismatch at {row['Chromosome']}:{pos}: VCF={ref}, FASTA={fasta_seq}, ALT={alt}")
    else:
        print(f"✅ Match at {row['Chromosome']}:{pos}: VCF={ref}, FASTA={fasta_seq}, ALT={alt}")


✅ Match at chr18:19791932: VCF=A, FASTA=A, ALT=T
✅ Match at chr18:19791935: VCF=C, FASTA=C, ALT=T
✅ Match at chr18:19791935: VCF=C, FASTA=C, ALT=A
✅ Match at chr18:19791936: VCF=G, FASTA=G, ALT=A
✅ Match at chr18:19791937: VCF=C, FASTA=C, ALT=A
✅ Match at chr18:19791941: VCF=C, FASTA=C, ALT=A
✅ Match at chr18:19791942: VCF=T, FASTA=T, ALT=A
✅ Match at chr18:19791945: VCF=G, FASTA=G, ALT=T
✅ Match at chr18:19791948: VCF=A, FASTA=A, ALT=T
✅ Match at chr18:19791949: VCF=G, FASTA=G, ALT=A
✅ Match at chr18:19791956: VCF=C, FASTA=C, ALT=A
✅ Match at chr18:19791958: VCF=G, FASTA=G, ALT=C
✅ Match at chr18:19791959: VCF=A, FASTA=A, ALT=C
✅ Match at chr18:19791961: VCF=G, FASTA=G, ALT=A
✅ Match at chr18:19791964: VCF=C, FASTA=C, ALT=G
✅ Match at chr18:19791967: VCF=A, FASTA=A, ALT=T
✅ Match at chr18:19791967: VCF=A, FASTA=A, ALT=C
✅ Match at chr18:19791970: VCF=C, FASTA=C, ALT=G
✅ Match at chr18:19791977: VCF=A, FASTA=A, ALT=G
✅ Match at chr18:19791991: VCF=C, FASTA=C, ALT=A
✅ Match at chr18:197

In [119]:
variants_df.duplicated(subset=["Chromosome", "Start"]).sum()

np.int64(1901)

In [120]:
variants_df.groupby(["Chromosome", "Start"]).size().reset_index(name="counts").query("counts > 1")

/scratch/tmp/l_schroeder/ipykernel_3949420/3226832589.py:1: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  variants_df.groupby(["Chromosome", "Start"]).size().reset_index(name="counts").query("counts > 1")


Chromosome     Start  counts
1          chr18  19791935       2
14         chr18  19791967       2
30         chr18  19792052       2
49         chr18  19792179       2
54         chr18  19792211       2
...          ...       ...     ...
49637      chr18  23911013       3
49671      chr18  23915650       2
49682      chr18  23916879       2
49683      chr18  23916883       2
49686      chr18  23916890       4

[1754 rows x 3 columns]